## Feature Engineering and Pre-Processing

In this jupyter notebook we will preprocess each DataFrame individually and then merge them into a single consolidated DataFrame (app) at the end. The merging process will involve the use of aggregations, groupby operations, and merge/join methods.

Since bureau_balance is associated with bureau_data, we will first merge these two DataFrames and then integrate the result with the app DataFrame. Although pos_cash_balance, credit_card_balance, and installments_payments are linked to previous_application, they each contain the SK_ID_CURR column, allowing us to join them directly with the app DataFrame.

The preprocessing steps we will follow for each DataFrame include:

1.Identifying and handling missing values above a threshold.

2.Addressing correlations that exceed a specified threshold.

3.Managing outliers.

4.Imputing missing values.

5.Encoding categorical variables.

6.Applying aggregations and groupby operations.

7.Checking for duplicates.

8.Identifying and handling constant values.

If any of these steps are skipped for a particular DataFrame, it indicates that the step is not relevant for that specific dataset. After preprocessing and merging all the DataFrames, we will perform another round of checks for these preprocessing steps.

Once preprocessing is complete, we will:

1.Apply a log transformation to the values.

2.Split the data into features (X) and the target variable (y).

3.Save the processed data for future use.

In [3]:
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
plt.style.use('fivethirtyeight')
plt.rcParams['font.size'] = 15
plt.rcParams['figure.figsize'] = (10, 6)
import seaborn as sns
pd.set_option('display.max_columns',None) 
import gc
import warnings
warnings.filterwarnings('ignore')

## One hot encoding

In [5]:
def one_hot_encoder(df):
    original_columns = list(df.columns)
    categorical_columns = [col for col in df.columns if df[col].dtype == 'object']
    df = pd.get_dummies(df, columns= categorical_columns)
    new_columns = [c for c in df.columns if c not in original_columns]
    return df, new_columns

From the below cells we will be preporcessing each file individually serial wise and at the end we will combine all the columns of each individual csv file in one csv and use that file for building model and hyperparameter tuning.

## 1.Bureau_Balance csv

In [8]:
bureau_balance = pd.read_csv('bureau_balance.csv')
bureau_balance.STATUS=bureau_balance.STATUS.map({'C':7,'X':6,'0':5,'1':4,'2':3,'3':2,'4':1,'5':0})

In [9]:
bureau_balance

SK_ID_BUREAU  MONTHS_BALANCE  STATUS
0              5715448               0       7
1              5715448              -1       7
2              5715448              -2       7
3              5715448              -3       7
4              5715448              -4       7
...                ...             ...     ...
27299920       5041336             -47       6
27299921       5041336             -48       6
27299922       5041336             -49       6
27299923       5041336             -50       6
27299924       5041336             -51       6

[27299925 rows x 3 columns]

## Aggregate and renaming columns

In [11]:
bureau_balance_aggregations = {'MONTHS_BALANCE': ['min', 'max', 'size','mean'],'STATUS':['mean','sum']}
bureau_balance_agg = bureau_balance.groupby('SK_ID_BUREAU').agg(bureau_balance_aggregations)
bureau_balance_agg.columns = pd.Index(['bureau_balance_'+e[0] + "_" + e[1].upper() for e in bureau_balance_agg.columns.tolist()])
bureau_balance_agg


bureau_balance_MONTHS_BALANCE_MIN  \
SK_ID_BUREAU                                      
5001709                                     -96   
5001710                                     -82   
5001711                                      -3   
5001712                                     -18   
5001713                                     -21   
...                                         ...   
6842884                                     -47   
6842885                                     -23   
6842886                                     -32   
6842887                                     -36   
6842888                                     -61   

              bureau_balance_MONTHS_BALANCE_MAX  \
SK_ID_BUREAU                                      
5001709                                       0   
5001710                                       0   
5001711                                       0   
5001712                                       0   
5001713                                       0   
...                                         ...   
6842884                                       0   
6842885                                       0   
6842886                                       0   
6842887                                       0   
6842888                                       0   

              bureau_balance_MONTHS_BALANCE_SIZE  \
SK_ID_BUREAU                                       
5001709                                       97   
5001710                                       83   
5001711                                        4   
5001712                                       19   
5001713                                       22   
...                                          ...   
6842884                                       48   
6842885                                       24   
6842886                                       33   
6842887                                       37   
6842888                                       62   

              bureau_balance_MONTHS_BALANCE_MEAN  bureau_balance_STATUS_MEAN  \
SK_ID_BUREAU                                                                   
5001709                                    -48.0                    6.886598   
5001710                                    -41.0                    6.518072   
5001711                                     -1.5                    5.250000   
5001712                                     -9.0                    5.947368   
5001713                                    -10.5                    6.000000   
...                                          ...                         ...   
6842884                                    -23.5                    6.229167   
6842885                                    -11.5                    2.500000   
6842886                                    -16.0                    6.515152   
6842887                                    -18.0                    6.675676   
6842888                                    -30.5                    6.661290   

              bureau_balance_STATUS_SUM  
SK_ID_BUREAU                             
5001709                             668  
5001710                             541  
5001711                              21  
5001712                             113  
5001713                             132  
...                                 ...  
6842884                             299  
6842885                              60  
6842886                             215  
6842887                             247  
6842888                             413  

[817395 rows x 6 columns]

we calculated aggregated statistics (min, max, size, mean, sum) for MONTHS_BALANCE and STATUS columns, grouped by SK_ID_BUREAU.


In [12]:
# Removing duplicate columns
_, idx = np.unique(bureau_balance_agg, axis = 1, return_index = True)
bureau_balance_agg = bureau_balance_agg.iloc[:, idx]
bureau_balance_agg

bureau_balance_MONTHS_BALANCE_MIN  \
SK_ID_BUREAU                                      
5001709                                     -96   
5001710                                     -82   
5001711                                      -3   
5001712                                     -18   
5001713                                     -21   
...                                         ...   
6842884                                     -47   
6842885                                     -23   
6842886                                     -32   
6842887                                     -36   
6842888                                     -61   

              bureau_balance_MONTHS_BALANCE_MEAN  \
SK_ID_BUREAU                                       
5001709                                    -48.0   
5001710                                    -41.0   
5001711                                     -1.5   
5001712                                     -9.0   
5001713                                    -10.5   
...                                          ...   
6842884                                    -23.5   
6842885                                    -11.5   
6842886                                    -16.0   
6842887                                    -18.0   
6842888                                    -30.5   

              bureau_balance_MONTHS_BALANCE_MAX  bureau_balance_STATUS_MEAN  \
SK_ID_BUREAU                                                                  
5001709                                       0                    6.886598   
5001710                                       0                    6.518072   
5001711                                       0                    5.250000   
5001712                                       0                    5.947368   
5001713                                       0                    6.000000   
...                                         ...                         ...   
6842884                                       0                    6.229167   
6842885                                       0                    2.500000   
6842886                                       0                    6.515152   
6842887                                       0                    6.675676   
6842888                                       0                    6.661290   

              bureau_balance_MONTHS_BALANCE_SIZE  bureau_balance_STATUS_SUM  
SK_ID_BUREAU                                                                 
5001709                                       97                        668  
5001710                                       83                        541  
5001711                                        4                         21  
5001712                                       19                        113  
5001713                                       22                        132  
...                                          ...                        ...  
6842884                                       48                        299  
6842885                                       24                         60  
6842886                                       33                        215  
6842887                                       37                        247  
6842888                                       62                        413  

[817395 rows x 6 columns]

In [13]:
bureau_balance_agg.std()

bureau_balance_MONTHS_BALANCE_MIN      28.132570
bureau_balance_MONTHS_BALANCE_MEAN     19.347775
bureau_balance_MONTHS_BALANCE_MAX      17.026851
bureau_balance_STATUS_MEAN              0.686313
bureau_balance_MONTHS_BALANCE_SIZE     25.794666
bureau_balance_STATUS_SUM             170.610017
dtype: float64

 the standard deviation for each column in the bureau_balance_agg 
 

In [14]:
bureau_balance_agg.isnull().sum().sum()

0

In [15]:
gc.enable()
del bureau_balance,bureau_balance_aggregations
gc.collect()

0

collecting garbage and deleting it

In [16]:
bureau_balance_agg

bureau_balance_MONTHS_BALANCE_MIN  \
SK_ID_BUREAU                                      
5001709                                     -96   
5001710                                     -82   
5001711                                      -3   
5001712                                     -18   
5001713                                     -21   
...                                         ...   
6842884                                     -47   
6842885                                     -23   
6842886                                     -32   
6842887                                     -36   
6842888                                     -61   

              bureau_balance_MONTHS_BALANCE_MEAN  \
SK_ID_BUREAU                                       
5001709                                    -48.0   
5001710                                    -41.0   
5001711                                     -1.5   
5001712                                     -9.0   
5001713                                    -10.5   
...                                          ...   
6842884                                    -23.5   
6842885                                    -11.5   
6842886                                    -16.0   
6842887                                    -18.0   
6842888                                    -30.5   

              bureau_balance_MONTHS_BALANCE_MAX  bureau_balance_STATUS_MEAN  \
SK_ID_BUREAU                                                                  
5001709                                       0                    6.886598   
5001710                                       0                    6.518072   
5001711                                       0                    5.250000   
5001712                                       0                    5.947368   
5001713                                       0                    6.000000   
...                                         ...                         ...   
6842884                                       0                    6.229167   
6842885                                       0                    2.500000   
6842886                                       0                    6.515152   
6842887                                       0                    6.675676   
6842888                                       0                    6.661290   

              bureau_balance_MONTHS_BALANCE_SIZE  bureau_balance_STATUS_SUM  
SK_ID_BUREAU                                                                 
5001709                                       97                        668  
5001710                                       83                        541  
5001711                                        4                         21  
5001712                                       19                        113  
5001713                                       22                        132  
...                                          ...                        ...  
6842884                                       48                        299  
6842885                                       24                         60  
6842886                                       33                        215  
6842887                                       37                        247  
6842888                                       62                        413  

[817395 rows x 6 columns]

## 2.Bureau csv

In [18]:
bureau = pd.read_csv('bureau.csv')
bureau

SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY  DAYS_CREDIT  \
0            215354       5714462        Closed      currency 1         -497   
1            215354       5714463        Active      currency 1         -208   
2            215354       5714464        Active      currency 1         -203   
3            215354       5714465        Active      currency 1         -203   
4            215354       5714466        Active      currency 1         -629   
...             ...           ...           ...             ...          ...   
1716423      259355       5057750        Active      currency 1          -44   
1716424      100044       5057754        Closed      currency 1        -2648   
1716425      100044       5057762        Closed      currency 1        -1809   
1716426      246829       5057770        Closed      currency 1        -1878   
1716427      246829       5057778        Closed      currency 1         -463   

         CREDIT_DAY_OVERDUE  DAYS_CREDIT_ENDDATE  DAYS_ENDDATE_FACT  \
0                         0               -153.0             -153.0   
1                         0               1075.0                NaN   
2                         0                528.0                NaN   
3                         0                  NaN                NaN   
4                         0               1197.0                NaN   
...                     ...                  ...                ...   
1716423                   0                -30.0                NaN   
1716424                   0              -2433.0            -2493.0   
1716425                   0              -1628.0             -970.0   
1716426                   0              -1513.0            -1513.0   
1716427                   0                  NaN             -387.0   

         AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
0                           NaN                   0        91323.00   
1                           NaN                   0       225000.00   
2                           NaN                   0       464323.50   
3                           NaN                   0        90000.00   
4                       77674.5                   0      2700000.00   
...                         ...                 ...             ...   
1716423                     0.0                   0        11250.00   
1716424                  5476.5                   0        38130.84   
1716425                     NaN                   0        15570.00   
1716426                     NaN                   0        36000.00   
1716427                     NaN                   0        22500.00   

         AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
0                        0.0                   NaN                     0.0   
1                   171342.0                   NaN                     0.0   
2                        NaN                   NaN                     0.0   
3                        NaN                   NaN                     0.0   
4                        NaN                   NaN                     0.0   
...                      ...                   ...                     ...   
1716423              11250.0                   0.0                     0.0   
1716424                  0.0                   0.0                     0.0   
1716425                  NaN                   NaN                     0.0   
1716426                  0.0                   0.0                     0.0   
1716427                  0.0                   NaN                     0.0   

             CREDIT_TYPE  DAYS_CREDIT_UPDATE  AMT_ANNUITY  
0        Consumer credit                -131          NaN  
1            Credit card                 -20          NaN  
2        Consumer credit                 -16          NaN  
3            Credit card                 -16          NaN  
4        Consumer credit                 -21          NaN  
...                  ...                 ... 

## Handling outliers

In [20]:
bureau.loc[(bureau.DAYS_ENDDATE_FACT<-40000),'DAYS_ENDDATE_FACT']=np.median(bureau.DAYS_ENDDATE_FACT)
bureau.loc[(bureau.DAYS_CREDIT_UPDATE<-40000),'DAYS_CREDIT_UPDATE']=np.median(bureau.DAYS_CREDIT_UPDATE)
bureau.loc[(bureau.DAYS_CREDIT_ENDDATE<-40000),'DAYS_CREDIT_ENDDATE']=np.median(bureau.DAYS_CREDIT_ENDDATE)
bureau.loc[(bureau.AMT_CREDIT_SUM_LIMIT>4000000),'AMT_CREDIT_SUM_LIMIT']=np.median(bureau.AMT_CREDIT_SUM_LIMIT)
bureau.loc[(bureau.AMT_CREDIT_SUM>4000000),'AMT_CREDIT_SUM']=np.median(bureau.AMT_CREDIT_SUM)
bureau.loc[(bureau.AMT_CREDIT_SUM_DEBT>4000000),'AMT_CREDIT_SUM_DEBT']=np.median(bureau.AMT_CREDIT_SUM_DEBT)

 handling outliers in the bureau DataFrame by replacing extreme values with the respective column's median. It adjusts both negative (DAYS_* columns) and excessively large (AMT_* columns) outliers to ensure data consistency and prevent skewed analysis.

In [21]:
bureau

SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY  DAYS_CREDIT  \
0            215354       5714462        Closed      currency 1         -497   
1            215354       5714463        Active      currency 1         -208   
2            215354       5714464        Active      currency 1         -203   
3            215354       5714465        Active      currency 1         -203   
4            215354       5714466        Active      currency 1         -629   
...             ...           ...           ...             ...          ...   
1716423      259355       5057750        Active      currency 1          -44   
1716424      100044       5057754        Closed      currency 1        -2648   
1716425      100044       5057762        Closed      currency 1        -1809   
1716426      246829       5057770        Closed      currency 1        -1878   
1716427      246829       5057778        Closed      currency 1         -463   

         CREDIT_DAY_OVERDUE  DAYS_CREDIT_ENDDATE  DAYS_ENDDATE_FACT  \
0                         0               -153.0             -153.0   
1                         0               1075.0                NaN   
2                         0                528.0                NaN   
3                         0                  NaN                NaN   
4                         0               1197.0                NaN   
...                     ...                  ...                ...   
1716423                   0                -30.0                NaN   
1716424                   0              -2433.0            -2493.0   
1716425                   0              -1628.0             -970.0   
1716426                   0              -1513.0            -1513.0   
1716427                   0                  NaN             -387.0   

         AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
0                           NaN                   0        91323.00   
1                           NaN                   0       225000.00   
2                           NaN                   0       464323.50   
3                           NaN                   0        90000.00   
4                       77674.5                   0      2700000.00   
...                         ...                 ...             ...   
1716423                     0.0                   0        11250.00   
1716424                  5476.5                   0        38130.84   
1716425                     NaN                   0        15570.00   
1716426                     NaN                   0        36000.00   
1716427                     NaN                   0        22500.00   

         AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
0                        0.0                   NaN                     0.0   
1                   171342.0                   NaN                     0.0   
2                        NaN                   NaN                     0.0   
3                        NaN                   NaN                     0.0   
4                        NaN                   NaN                     0.0   
...                      ...                   ...                     ...   
1716423              11250.0                   0.0                     0.0   
1716424                  0.0                   0.0                     0.0   
1716425                  NaN                   NaN                     0.0   
1716426                  0.0                   0.0                     0.0   
1716427                  0.0                   NaN                     0.0   

             CREDIT_TYPE  DAYS_CREDIT_UPDATE  AMT_ANNUITY  
0        Consumer credit                -131          NaN  
1            Credit card                 -20          NaN  
2        Consumer credit                 -16          NaN  
3            Credit card                 -16          NaN  
4        Consumer credit                 -21          NaN  
...                  ...                 ... 

In [22]:

bureau_features_with_na=[features for features in bureau.columns if bureau[features].isnull().sum()>0] 
print('The Features that have missing values are as follows: \n',bureau_features_with_na)
print('The number of Features with missing values are:',len(bureau_features_with_na))

The Features that have missing values are as follows: 
 ['DAYS_CREDIT_ENDDATE', 'DAYS_ENDDATE_FACT', 'AMT_CREDIT_MAX_OVERDUE', 'AMT_CREDIT_SUM', 'AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT', 'AMT_ANNUITY']
The number of Features with missing values are: 7


In [23]:
bureau.DAYS_ENDDATE_FACT=bureau.DAYS_ENDDATE_FACT.fillna(0)
bureau['DAYS_CREDIT_ENDDATE'] = bureau['DAYS_CREDIT_ENDDATE'].fillna(bureau['DAYS_CREDIT_ENDDATE'].median())
bureau['AMT_CREDIT_MAX_OVERDUE'] = bureau['AMT_CREDIT_MAX_OVERDUE'].fillna(bureau['AMT_CREDIT_MAX_OVERDUE'].median())
bureau['AMT_CREDIT_SUM'] = bureau['AMT_CREDIT_SUM'].fillna(bureau['AMT_CREDIT_SUM'].median())
bureau['AMT_CREDIT_SUM_DEBT'] = bureau['AMT_CREDIT_SUM_DEBT'].fillna(bureau['AMT_CREDIT_SUM_DEBT'].median())
bureau['AMT_CREDIT_SUM_LIMIT'] = bureau['AMT_CREDIT_SUM_LIMIT'].fillna(bureau['AMT_CREDIT_SUM_LIMIT'].median())
bureau['AMT_ANNUITY'] = bureau['AMT_ANNUITY'].fillna(bureau['AMT_ANNUITY'].median())

 filling missing values (NaN) in the bureau DataFrame. It replaces DAYS_ENDDATE_FACT with 0, while other columns like DAYS_CREDIT_ENDDATE, AMT_* columns, and AMT_ANNUITY are filled with their respective medians ensuring that the dataset has no missing values for further analysis.

In [24]:
bureau.isnull().sum().sum()


0

## Adding new feature

In [26]:
bureau['LOAN_RATE'] = bureau['AMT_ANNUITY'] / (1 + bureau['AMT_CREDIT_SUM'])

creating a new column, LOAN_RATE, by calculating the ratio of AMT_ANNUITY to the sum of AMT_CREDIT_SUM plus 1. This represents the annual payment-to-credit ratio for each loan in the bureau DataFrame.

In [27]:
## one hot encoding the categorical column
bureau.CREDIT_ACTIVE=bureau.CREDIT_ACTIVE.map({'Closed':3,'Active':2,'Sold':1,'Bad debt':0})
bureau, bureau_cat = one_hot_encoder(bureau) 

In [28]:
bureau

SK_ID_CURR  SK_ID_BUREAU  CREDIT_ACTIVE  DAYS_CREDIT  \
0            215354       5714462              3         -497   
1            215354       5714463              2         -208   
2            215354       5714464              2         -203   
3            215354       5714465              2         -203   
4            215354       5714466              2         -629   
...             ...           ...            ...          ...   
1716423      259355       5057750              2          -44   
1716424      100044       5057754              3        -2648   
1716425      100044       5057762              3        -1809   
1716426      246829       5057770              3        -1878   
1716427      246829       5057778              3         -463   

         CREDIT_DAY_OVERDUE  DAYS_CREDIT_ENDDATE  DAYS_ENDDATE_FACT  \
0                         0               -153.0             -153.0   
1                         0               1075.0                0.0   
2                         0                528.0                0.0   
3                         0               -330.0                0.0   
4                         0               1197.0                0.0   
...                     ...                  ...                ...   
1716423                   0                -30.0                0.0   
1716424                   0              -2433.0            -2493.0   
1716425                   0              -1628.0             -970.0   
1716426                   0              -1513.0            -1513.0   
1716427                   0               -330.0             -387.0   

         AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
0                           0.0                   0        91323.00   
1                           0.0                   0       225000.00   
2                           0.0                   0       464323.50   
3                           0.0                   0        90000.00   
4                       77674.5                   0      2700000.00   
...                         ...                 ...             ...   
1716423                     0.0                   0        11250.00   
1716424                  5476.5                   0        38130.84   
1716425                     0.0                   0        15570.00   
1716426                     0.0                   0        36000.00   
1716427                     0.0                   0        22500.00   

         AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
0                        0.0                   0.0                     0.0   
1                   171342.0                   0.0                     0.0   
2                        0.0                   0.0                     0.0   
3                        0.0                   0.0                     0.0   
4                        0.0                   0.0                     0.0   
...                      ...                   ...                     ...   
1716423              11250.0                   0.0                     0.0   
1716424                  0.0                   0.0                     0.0   
1716425                  0.0                   0.0                     0.0   
1716426                  0.0                   0.0                     0.0   
1716427                  0.0                   0.0                     0.0   

         DAYS_CREDIT_UPDATE  AMT_ANNUITY  LOAN_RATE  \
0                      -131          0.0        0.0   
1                       -20          0.0        0.0   
2                       -16          0.0        0.0   
3                       -16          0.0        0.0   
4                       -21          0.0        0.0   
...                     ...          ...        ...   
1716423                 -19          0.0        0.0   
1716424               -2493          0.0        0.0   
1716425                -967          0.0        0.0   
1716426               -1508        

In [29]:
bureau_cat

['CREDIT_CURRENCY_currency 1',
 'CREDIT_CURRENCY_currency 2',
 'CREDIT_CURRENCY_currency 3',
 'CREDIT_CURRENCY_currency 4',
 'CREDIT_TYPE_Another type of loan',
 'CREDIT_TYPE_Car loan',
 'CREDIT_TYPE_Cash loan (non-earmarked)',
 'CREDIT_TYPE_Consumer credit',
 'CREDIT_TYPE_Credit card',
 'CREDIT_TYPE_Interbank credit',
 'CREDIT_TYPE_Loan for business development',
 'CREDIT_TYPE_Loan for purchase of shares (margin lending)',
 'CREDIT_TYPE_Loan for the purchase of equipment',
 'CREDIT_TYPE_Loan for working capital replenishment',
 'CREDIT_TYPE_Microloan',
 'CREDIT_TYPE_Mobile operator loan',
 'CREDIT_TYPE_Mortgage',
 'CREDIT_TYPE_Real estate loan',
 'CREDIT_TYPE_Unknown type of loan']

In [30]:
bureau = bureau.join(bureau_balance_agg, how='left', on='SK_ID_BUREAU')
bureau

SK_ID_CURR  SK_ID_BUREAU  CREDIT_ACTIVE  DAYS_CREDIT  \
0            215354       5714462              3         -497   
1            215354       5714463              2         -208   
2            215354       5714464              2         -203   
3            215354       5714465              2         -203   
4            215354       5714466              2         -629   
...             ...           ...            ...          ...   
1716423      259355       5057750              2          -44   
1716424      100044       5057754              3        -2648   
1716425      100044       5057762              3        -1809   
1716426      246829       5057770              3        -1878   
1716427      246829       5057778              3         -463   

         CREDIT_DAY_OVERDUE  DAYS_CREDIT_ENDDATE  DAYS_ENDDATE_FACT  \
0                         0               -153.0             -153.0   
1                         0               1075.0                0.0   
2                         0                528.0                0.0   
3                         0               -330.0                0.0   
4                         0               1197.0                0.0   
...                     ...                  ...                ...   
1716423                   0                -30.0                0.0   
1716424                   0              -2433.0            -2493.0   
1716425                   0              -1628.0             -970.0   
1716426                   0              -1513.0            -1513.0   
1716427                   0               -330.0             -387.0   

         AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
0                           0.0                   0        91323.00   
1                           0.0                   0       225000.00   
2                           0.0                   0       464323.50   
3                           0.0                   0        90000.00   
4                       77674.5                   0      2700000.00   
...                         ...                 ...             ...   
1716423                     0.0                   0        11250.00   
1716424                  5476.5                   0        38130.84   
1716425                     0.0                   0        15570.00   
1716426                     0.0                   0        36000.00   
1716427                     0.0                   0        22500.00   

         AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
0                        0.0                   0.0                     0.0   
1                   171342.0                   0.0                     0.0   
2                        0.0                   0.0                     0.0   
3                        0.0                   0.0                     0.0   
4                        0.0                   0.0                     0.0   
...                      ...                   ...                     ...   
1716423              11250.0                   0.0                     0.0   
1716424                  0.0                   0.0                     0.0   
1716425                  0.0                   0.0                     0.0   
1716426                  0.0                   0.0                     0.0   
1716427                  0.0                   0.0                     0.0   

         DAYS_CREDIT_UPDATE  AMT_ANNUITY  LOAN_RATE  \
0                      -131          0.0        0.0   
1                       -20          0.0        0.0   
2                       -16          0.0        0.0   
3                       -16          0.0        0.0   
4                       -21          0.0        0.0   
...                     ...          ...        ...   
1716423                 -19          0.0        0.0   
1716424               -2493          0.0        0.0   
1716425                -967          0.0        0.0   
1716426               -1508        

Joining the bureau column and bureau balance column using left join and primary column as SK_ID_BUREAU

In [31]:
# Handling missing values
bureau=bureau.fillna(0) 
bureau.head(20)

SK_ID_CURR  SK_ID_BUREAU  CREDIT_ACTIVE  DAYS_CREDIT  CREDIT_DAY_OVERDUE  \
0       215354       5714462              3         -497                   0   
1       215354       5714463              2         -208                   0   
2       215354       5714464              2         -203                   0   
3       215354       5714465              2         -203                   0   
4       215354       5714466              2         -629                   0   
5       215354       5714467              2         -273                   0   
6       215354       5714468              2          -43                   0   
7       162297       5714469              3        -1896                   0   
8       162297       5714470              3        -1146                   0   
9       162297       5714471              2        -1146                   0   
10      162297       5714472              2        -1146                   0   
11      162297       5714473              3        -2456                   0   
12      162297       5714474              2         -277                   0   
13      402440       5714475              2          -96                   0   
14      238881       5714482              3         -318                   0   
15      238881       5714484              3        -2911                   0   
16      238881       5714485              3        -2148                   0   
17      238881       5714486              2         -381                   0   
18      238881       5714487              2          -95                   0   
19      238881       5714488              3         -444                   0   

    DAYS_CREDIT_ENDDATE  DAYS_ENDDATE_FACT  AMT_CREDIT_MAX_OVERDUE  \
0                -153.0             -153.0                     0.0   
1                1075.0                0.0                     0.0   
2                 528.0                0.0                     0.0   
3                -330.0                0.0                     0.0   
4                1197.0                0.0                 77674.5   
5               27460.0                0.0                     0.0   
6                  79.0                0.0                     0.0   
7               -1684.0            -1710.0                 14985.0   
8                -811.0             -840.0                     0.0   
9                -484.0                0.0                     0.0   
10               -180.0                0.0                     0.0   
11               -629.0             -825.0                     0.0   
12               5261.0                0.0                     0.0   
13                269.0                0.0                     0.0   
14               -187.0             -187.0                     0.0   
15              -2607.0            -2604.0                     0.0   
16              -1595.0             -987.0                     0.0   
17               -330.0                0.0                     0.0   
18               1720.0                0.0                     0.0   
19                -77.0              -77.0                     0.0   

    CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  AMT_CREDIT_SUM_DEBT  \
0                    0        91323.00                 0.00   
1                    0       225000.00            171342.00   
2                    0       464323.50                 0.00   
3                    0        90000.00                 0.00   
4                    0      2700000.00                 0.00   
5                    0       180000.00             71017.38   
6                    0        42103.80             42103.80   
7                    0        76878.45                 0.00   
8                    0       103007.70                 0.00   
9                    0         4500.00                 0.00   
10                   0       337500.00                 0.00   
11                   0       675000.00                 0.00   
12                   0       1223

In [32]:
bureau.std()

SK_ID_CURR                                                  102938.558112
SK_ID_BUREAU                                                532265.728552
CREDIT_ACTIVE                                                    0.491999
DAYS_CREDIT                                                    795.164928
CREDIT_DAY_OVERDUE                                              36.544428
DAYS_CREDIT_ENDDATE                                           4827.981452
DAYS_ENDDATE_FACT                                              749.455048
AMT_CREDIT_MAX_OVERDUE                                      121006.498427
CNT_CREDIT_PROLONG                                               0.096224
AMT_CREDIT_SUM                                              466292.361955
AMT_CREDIT_SUM_DEBT                                         304058.061692
AMT_CREDIT_SUM_LIMIT                                         35910.671411
AMT_CREDIT_SUM_OVERDUE                                        5937.650035
DAYS_CREDIT_UPDATE                    

In [33]:
bureau.drop(['SK_ID_BUREAU'], axis=1, inplace= True)

as we have joined the two csv files so there is no need for "SK_ID_bureau" column

In [34]:
bureau_combined_col=[feature for feature in bureau.columns if feature not in 'SK_ID_CURR']
bureau_aggregations = {}
for col in bureau_combined_col:
    bureau_aggregations[col] = ['min','max','mean','sum']
bureau_agg = bureau.groupby('SK_ID_CURR').agg(bureau_aggregations)
bureau_agg

CREDIT_ACTIVE                   DAYS_CREDIT                     \
                     min max      mean sum         min   max         mean   
SK_ID_CURR                                                                  
100001                 2   3  2.571429  18       -1572   -49  -735.000000   
100002                 2   3  2.750000  22       -1437  -103  -874.000000   
100003                 2   3  2.750000  11       -2586  -606 -1400.750000   
100004                 3   3  3.000000   6       -1326  -408  -867.000000   
100005                 2   3  2.333333   7        -373   -62  -190.666667   
...                  ...  ..       ...  ..         ...   ...          ...   
456249                 2   3  2.846154  37       -2713  -483 -1667.076923   
456250                 2   3  2.333333   7       -1002  -760  -862.000000   
456253                 2   3  2.500000  10        -919  -713  -867.500000   
456254                 3   3  3.000000   3       -1104 -1104 -1104.000000   
456255                 2   3  2.545455  28       -2337  -363 -1089.454545   

                  CREDIT_DAY_OVERDUE              DAYS_CREDIT_ENDDATE  \
              sum                min max mean sum                 min   
SK_ID_CURR                                                              
100001      -5145                  0   0  0.0   0             -1329.0   
100002      -6992                  0   0  0.0   0             -1072.0   
100003      -5603                  0   0  0.0   0             -2434.0   
100004      -1734                  0   0  0.0   0              -595.0   
100005       -572                  0   0  0.0   0              -128.0   
...           ...                ...  ..  ...  ..                 ...   
456249     -21672                  0   0  0.0   0             -2499.0   
456250      -2586                  0   0  0.0   0              -272.0   
456253      -3470                  0   0  0.0   0              -189.0   
456254      -1104                  0   0  0.0   0              -859.0   
456255     -11984                  0   0  0.0   0             -1243.0   

                                          DAYS_ENDDATE_FACT         \
                max         mean      sum               min    max   
SK_ID_CURR                                                           
100001       1778.0    82.428571    577.0           -1328.0    0.0   
100002        780.0  -344.250000  -2754.0           -1185.0    0.0   
100003       1216.0  -544.500000  -2178.0           -2131.0    0.0   
100004       -382.0  -488.500000   -977.0            -683.0 -382.0   
100005       1324.0   439.333333   1318.0            -123.0    0.0   
...             ...          ...      ...               ...    ...   
456249       1363.0 -1162.923077 -15118.0           -2525.0    0.0   
456250       2340.0  1288.333333   3865.0            -760.0    0.0   
456253       1113.0   280.500000   1122.0            -794.0    0.0   
456254       -859.0  -859.000000   -859.0            -859.0 -859.0   
456255      27320.0  3231.272727  35544.0           -1621.0    0.0   

                                 AMT_CREDIT_MAX_OVERDUE             \
                   mean      sum                    min        max   
SK_ID_CURR                                                           
100001      -471.714286  -3302.0                    0.0      0.000   
100002      -523.125000  -4185.0                    0.0   5043.645   
100003      -823.000000  -3292.0                    0.0      0.000   
100004      -532.500000  -1065.0                    0.0      0.000   
100005       -41.000000   -123.0                    0.0      0.000   
...                 ...      ...                    ...        ...   
456249     -1259.769231 -16377.0                    0.0  18945.000   
456250      -253.333333   -760.0                    0.0      0.000   
456253      -397.000000  -1588.0                    0.0      0.000   
456254      -859.000000   -859.0                    0.0      0.000   
456255      -528.1

creating a list of columns from bureau . It then defines aggregation functions (min, max, mean, sum) for each of these columns and applies them, grouping by SK_ID_CURR. The result is a DataFrame bureau_agg, which contains aggregated statistics for each SK_ID_CURR.

In [35]:
bureau_agg.columns = pd.Index(['bureau_'+e[0] + "_" + e[1].upper() for e in bureau_agg.columns.tolist()])
bureau_agg

bureau_CREDIT_ACTIVE_MIN  bureau_CREDIT_ACTIVE_MAX  \
SK_ID_CURR                                                       
100001                             2                         3   
100002                             2                         3   
100003                             2                         3   
100004                             3                         3   
100005                             2                         3   
...                              ...                       ...   
456249                             2                         3   
456250                             2                         3   
456253                             2                         3   
456254                             3                         3   
456255                             2                         3   

            bureau_CREDIT_ACTIVE_MEAN  bureau_CREDIT_ACTIVE_SUM  \
SK_ID_CURR                                                        
100001                       2.571429                        18   
100002                       2.750000                        22   
100003                       2.750000                        11   
100004                       3.000000                         6   
100005                       2.333333                         7   
...                               ...                       ...   
456249                       2.846154                        37   
456250                       2.333333                         7   
456253                       2.500000                        10   
456254                       3.000000                         3   
456255                       2.545455                        28   

            bureau_DAYS_CREDIT_MIN  bureau_DAYS_CREDIT_MAX  \
SK_ID_CURR                                                   
100001                       -1572                     -49   
100002                       -1437                    -103   
100003                       -2586                    -606   
100004                       -1326                    -408   
100005                        -373                     -62   
...                            ...                     ...   
456249                       -2713                    -483   
456250                       -1002                    -760   
456253                        -919                    -713   
456254                       -1104                   -1104   
456255                       -2337                    -363   

            bureau_DAYS_CREDIT_MEAN  bureau_DAYS_CREDIT_SUM  \
SK_ID_CURR                                                    
100001                  -735.000000                   -5145   
100002                  -874.000000                   -6992   
100003                 -1400.750000                   -5603   
100004                  -867.000000                   -1734   
100005                  -190.666667                    -572   
...                             ...                     ...   
456249                 -1667.076923                  -21672   
456250                  -862.000000                   -2586   
456253                  -867.500000                   -3470   
456254                 -1104.000000                   -1104   
456255                 -1089.454545                  -11984   

            bureau_CREDIT_DAY_OVERDUE_MIN  bureau_CREDIT_DAY_OVERDUE_MAX  \
SK_ID_CURR                                                                 
100001                                  0                              0   
100002                                  0                              0   
100003                                  0                              0   
100004                                  0                              0   
100005                                  0                              0   
...                                   ...                            ...   
456249                                  0     

renaming the columns in bureau_agg by concatenating the prefix bureau_, the column name, and the aggregation method (e.g., min, max, mean, sum). This ensures the column names are descriptive and reflect the applied aggregation, making it easier to understand the transformations in the dataset.

In [36]:
_, idx = np.unique(bureau_agg.columns, return_index=True)

# Select columns with unique names based on the index
bureau_agg = bureau_agg.iloc[:, sorted(idx)]
bureau_agg

bureau_CREDIT_ACTIVE_MIN  bureau_CREDIT_ACTIVE_MAX  \
SK_ID_CURR                                                       
100001                             2                         3   
100002                             2                         3   
100003                             2                         3   
100004                             3                         3   
100005                             2                         3   
...                              ...                       ...   
456249                             2                         3   
456250                             2                         3   
456253                             2                         3   
456254                             3                         3   
456255                             2                         3   

            bureau_CREDIT_ACTIVE_MEAN  bureau_CREDIT_ACTIVE_SUM  \
SK_ID_CURR                                                        
100001                       2.571429                        18   
100002                       2.750000                        22   
100003                       2.750000                        11   
100004                       3.000000                         6   
100005                       2.333333                         7   
...                               ...                       ...   
456249                       2.846154                        37   
456250                       2.333333                         7   
456253                       2.500000                        10   
456254                       3.000000                         3   
456255                       2.545455                        28   

            bureau_DAYS_CREDIT_MIN  bureau_DAYS_CREDIT_MAX  \
SK_ID_CURR                                                   
100001                       -1572                     -49   
100002                       -1437                    -103   
100003                       -2586                    -606   
100004                       -1326                    -408   
100005                        -373                     -62   
...                            ...                     ...   
456249                       -2713                    -483   
456250                       -1002                    -760   
456253                        -919                    -713   
456254                       -1104                   -1104   
456255                       -2337                    -363   

            bureau_DAYS_CREDIT_MEAN  bureau_DAYS_CREDIT_SUM  \
SK_ID_CURR                                                    
100001                  -735.000000                   -5145   
100002                  -874.000000                   -6992   
100003                 -1400.750000                   -5603   
100004                  -867.000000                   -1734   
100005                  -190.666667                    -572   
...                             ...                     ...   
456249                 -1667.076923                  -21672   
456250                  -862.000000                   -2586   
456253                  -867.500000                   -3470   
456254                 -1104.000000                   -1104   
456255                 -1089.454545                  -11984   

            bureau_CREDIT_DAY_OVERDUE_MIN  bureau_CREDIT_DAY_OVERDUE_MAX  \
SK_ID_CURR                                                                 
100001                                  0                              0   
100002                                  0                              0   
100003                                  0                              0   
100004                                  0                              0   
100005                                  0                              0   
...                                   ...                            ...   
456249                                  0     

In [37]:
bureau_agg = bureau_agg.loc[:, ~bureau_agg.T.duplicated()]

Removing duplicate columns for better optimization



In [38]:
bureau_agg

bureau_CREDIT_ACTIVE_MIN  bureau_CREDIT_ACTIVE_MAX  \
SK_ID_CURR                                                       
100001                             2                         3   
100002                             2                         3   
100003                             2                         3   
100004                             3                         3   
100005                             2                         3   
...                              ...                       ...   
456249                             2                         3   
456250                             2                         3   
456253                             2                         3   
456254                             3                         3   
456255                             2                         3   

            bureau_CREDIT_ACTIVE_MEAN  bureau_CREDIT_ACTIVE_SUM  \
SK_ID_CURR                                                        
100001                       2.571429                        18   
100002                       2.750000                        22   
100003                       2.750000                        11   
100004                       3.000000                         6   
100005                       2.333333                         7   
...                               ...                       ...   
456249                       2.846154                        37   
456250                       2.333333                         7   
456253                       2.500000                        10   
456254                       3.000000                         3   
456255                       2.545455                        28   

            bureau_DAYS_CREDIT_MIN  bureau_DAYS_CREDIT_MAX  \
SK_ID_CURR                                                   
100001                       -1572                     -49   
100002                       -1437                    -103   
100003                       -2586                    -606   
100004                       -1326                    -408   
100005                        -373                     -62   
...                            ...                     ...   
456249                       -2713                    -483   
456250                       -1002                    -760   
456253                        -919                    -713   
456254                       -1104                   -1104   
456255                       -2337                    -363   

            bureau_DAYS_CREDIT_MEAN  bureau_DAYS_CREDIT_SUM  \
SK_ID_CURR                                                    
100001                  -735.000000                   -5145   
100002                  -874.000000                   -6992   
100003                 -1400.750000                   -5603   
100004                  -867.000000                   -1734   
100005                  -190.666667                    -572   
...                             ...                     ...   
456249                 -1667.076923                  -21672   
456250                  -862.000000                   -2586   
456253                  -867.500000                   -3470   
456254                 -1104.000000                   -1104   
456255                 -1089.454545                  -11984   

            bureau_CREDIT_DAY_OVERDUE_MIN  bureau_CREDIT_DAY_OVERDUE_MAX  \
SK_ID_CURR                                                                 
100001                                  0                              0   
100002                                  0                              0   
100003                                  0                              0   
100004                                  0                              0   
100005                                  0                              0   
...                                   ...                            ...   
456249                                  0     

In [39]:
bureau_agg.isnull().sum().sum()

0

In [40]:
pd.set_option('display.max_rows',None) 

In [41]:
bureau_agg.std()

bureau_CREDIT_ACTIVE_MIN                                                4.124753e-01
bureau_CREDIT_ACTIVE_MAX                                                3.320474e-01
bureau_CREDIT_ACTIVE_MEAN                                               3.123925e-01
bureau_CREDIT_ACTIVE_SUM                                                1.208982e+01
bureau_DAYS_CREDIT_MIN                                                  8.592608e+02
bureau_DAYS_CREDIT_MAX                                                  5.335293e+02
bureau_DAYS_CREDIT_MEAN                                                 5.584411e+02
bureau_DAYS_CREDIT_SUM                                                  6.097186e+03
bureau_CREDIT_DAY_OVERDUE_MIN                                           1.649230e+01
bureau_CREDIT_DAY_OVERDUE_MAX                                           8.557359e+01
bureau_CREDIT_DAY_OVERDUE_MEAN                                          2.495721e+01
bureau_CREDIT_DAY_OVERDUE_SUM                                    

In [42]:
pd.reset_option('display.max_rows') 

In [43]:
bureau_agg=bureau_agg.drop(columns='bureau_CREDIT_CURRENCY_currency 4_MIN')
bureau_agg.info()

<class 'pandas.core.frame.DataFrame'>
Index: 305811 entries, 100001 to 456255
Columns: 147 entries, bureau_CREDIT_ACTIVE_MIN to bureau_bureau_balance_STATUS_SUM_SUM
dtypes: bool(34), float64(84), int64(29)
memory usage: 284.0 MB


In [44]:
gc.enable()
del bureau_balance_agg,bureau,bureau_cat,bureau_combined_col,bureau_aggregations
gc.collect()

0

## 3. Pos_cash_balance csv

In [46]:
pos_cash_balance = pd.read_csv('POS_CASH_balance.csv')
pos_cash_balance.NAME_CONTRACT_STATUS=pos_cash_balance.NAME_CONTRACT_STATUS.map({'Completed':8,'Active':7,'Signed':6,'Approved':5,'Canceled':4,'Returned to the store':3,'Demand':2,'XNA':1,'Amortized debt':0})
pos_cash_balance

SK_ID_PREV  SK_ID_CURR  MONTHS_BALANCE  CNT_INSTALMENT  \
0            1803195      182943             -31            48.0   
1            1715348      367990             -33            36.0   
2            1784872      397406             -32            12.0   
3            1903291      269225             -35            48.0   
4            2341044      334279             -35            36.0   
...              ...         ...             ...             ...   
10001353     2448283      226558             -20             6.0   
10001354     1717234      141565             -19            12.0   
10001355     1283126      315695             -21            10.0   
10001356     1082516      450255             -22            12.0   
10001357     1259607      174278             -52            16.0   

          CNT_INSTALMENT_FUTURE  NAME_CONTRACT_STATUS  SK_DPD  SK_DPD_DEF  
0                          45.0                     7       0           0  
1                          35.0                     7       0           0  
2                           9.0                     7       0           0  
3                          42.0                     7       0           0  
4                          35.0                     7       0           0  
...                         ...                   ...     ...         ...  
10001353                    0.0                     7     843           0  
10001354                    0.0                     7     602           0  
10001355                    0.0                     7     609           0  
10001356                    0.0                     7     614           0  
10001357                    0.0                     8       0           0  

[10001358 rows x 8 columns]

In [47]:
## Handling outliers
pos_cash_balance.loc[(pos_cash_balance.CNT_INSTALMENT>75.0),'CNT_INSTALMENT']=np.median(pos_cash_balance.CNT_INSTALMENT)
pos_cash_balance.loc[(pos_cash_balance.CNT_INSTALMENT_FUTURE>75.0),'CNT_INSTALMENT_FUTURE']=np.median(pos_cash_balance.CNT_INSTALMENT_FUTURE)

 replacing extreme values (greater than 75.0) in the CNT_INSTALMENT and CNT_INSTALMENT_FUTURE columns of the pos_cash_balance DataFrame with the median of their respective columns. This helps in handling outliers and ensures the data is more consistent for analysis or modeling.

In [48]:
## Handling missing values
pos_cash_balance_features_with_na=[features for features in pos_cash_balance.columns if pos_cash_balance[features].isnull().sum()>0] 
print('The Features that have missing values are as follows: \n',pos_cash_balance_features_with_na)
print('The number of Features with missing values are:',len(pos_cash_balance_features_with_na))

The Features that have missing values are as follows: 
 ['CNT_INSTALMENT', 'CNT_INSTALMENT_FUTURE']
The number of Features with missing values are: 2


In [49]:

pos_cash_balance['CNT_INSTALMENT'] = pos_cash_balance['CNT_INSTALMENT'].fillna(0)
pos_cash_balance['CNT_INSTALMENT_FUTURE'] = pos_cash_balance['CNT_INSTALMENT_FUTURE'].fillna(0)

In [50]:
pos_cash_balance.isnull().sum().sum()

0

## Adding new feature

In [52]:
pos_cash_balance['INSTALLMENTS_PAID'] = pos_cash_balance['CNT_INSTALMENT'] - pos_cash_balance['CNT_INSTALMENT_FUTURE']
pos_cash_balance

SK_ID_PREV  SK_ID_CURR  MONTHS_BALANCE  CNT_INSTALMENT  \
0            1803195      182943             -31            48.0   
1            1715348      367990             -33            36.0   
2            1784872      397406             -32            12.0   
3            1903291      269225             -35            48.0   
4            2341044      334279             -35            36.0   
...              ...         ...             ...             ...   
10001353     2448283      226558             -20             6.0   
10001354     1717234      141565             -19            12.0   
10001355     1283126      315695             -21            10.0   
10001356     1082516      450255             -22            12.0   
10001357     1259607      174278             -52            16.0   

          CNT_INSTALMENT_FUTURE  NAME_CONTRACT_STATUS  SK_DPD  SK_DPD_DEF  \
0                          45.0                     7       0           0   
1                          35.0                     7       0           0   
2                           9.0                     7       0           0   
3                          42.0                     7       0           0   
4                          35.0                     7       0           0   
...                         ...                   ...     ...         ...   
10001353                    0.0                     7     843           0   
10001354                    0.0                     7     602           0   
10001355                    0.0                     7     609           0   
10001356                    0.0                     7     614           0   
10001357                    0.0                     8       0           0   

          INSTALLMENTS_PAID  
0                       3.0  
1                       1.0  
2                       3.0  
3                       6.0  
4                       1.0  
...                     ...  
10001353                6.0  
10001354               12.0  
10001355               10.0  
10001356               12.0  
10001357               16.0  

[10001358 rows x 9 columns]

creating a new column, INSTALLMENTS_PAID, by calculating the difference between CNT_INSTALMENT and CNT_INSTALMENT_FUTURE. It represents the number of installments that have already been paid versus those yet to be paid

In [53]:
pos_cash_balance_aggregations = {'MONTHS_BALANCE': ['min', 'max', 'size','mean'],
                      'CNT_INSTALMENT': ['min', 'max', 'size','mean'],
                      'CNT_INSTALMENT_FUTURE': ['min', 'max', 'size','mean'],
                      'SK_DPD': ['min', 'max', 'size','mean'],
                      'SK_DPD_DEF': ['min', 'max', 'size','mean'],
                      'INSTALLMENTS_PAID': ['min', 'max', 'size','mean'], 'SK_ID_PREV': ['size'], 
                      'NAME_CONTRACT_STATUS':['mean','sum']}
pos_cash_balance_agg = pos_cash_balance.groupby('SK_ID_CURR').agg(pos_cash_balance_aggregations)
pos_cash_balance_agg

MONTHS_BALANCE                     CNT_INSTALMENT             \
                      min max size       mean            min   max size   
SK_ID_CURR                                                                
100001                -96 -53    9 -72.555556            4.0   4.0    9   
100002                -19  -1   19 -10.000000           24.0  24.0   19   
100003                -77 -18   28 -43.785714            6.0  12.0   28   
100004                -27 -24    4 -25.500000            3.0   4.0    4   
100005                -25 -15   11 -20.000000            0.0  12.0   11   
...                   ...  ..  ...        ...            ...   ...  ...   
456251                 -9  -1    9  -5.000000            0.0   8.0    9   
456252                -82 -76    7 -79.000000            6.0   6.0    7   
456253                -96 -57   17 -79.235294            4.0  12.0   17   
456254                -11  -1   20  -5.550000           14.0  16.0   20   
456255                -33  -2   71 -16.408451            3.0  36.0   71   

                      CNT_INSTALMENT_FUTURE                       SK_DPD      \
                 mean                   min   max size       mean    min max   
SK_ID_CURR                                                                     
100001       4.000000                   0.0   4.0    9   1.444444      0   7   
100002      24.000000                   6.0  24.0   19  15.000000      0   0   
100003      10.107143                   0.0  12.0   28   5.785714      0   0   
100004       3.750000                   0.0   4.0    4   2.250000      0   0   
100005      10.636364                   0.0  12.0   11   6.545455      0   0   
...               ...                   ...   ...  ...        ...    ...  ..   
456251       7.000000                   0.0   8.0    9   3.888889      0   0   
456252       6.000000                   0.0   6.0    7   3.000000      0   0   
456253       6.705882                   0.0   6.0   17   2.000000      0   5   
456254      14.900000                   4.0  16.0   20  10.350000      0   0   
456255      22.788732                   0.0  36.0   71  15.140845      0   5   

                          SK_DPD_DEF                    INSTALLMENTS_PAID  \
           size      mean        min max size      mean               min   
SK_ID_CURR                                                                  
100001        9  0.777778          0   7    9  0.777778               0.0   
100002       19  0.000000          0   0   19  0.000000               0.0   
100003       28  0.000000          0   0   28  0.000000               0.0   
100004        4  0.000000          0   0    4  0.000000               0.0   
100005       11  0.000000          0   0   11  0.000000               0.0   
...         ...       ...        ...  ..  ...       ...               ...   
456251        9  0.000000          0   0    9  0.000000               0.0   
456252        7  0.000000          0   0    7  0.000000               0.0   
456253       17  0.294118          0   5   17  0.294118               0.0   
456254       20  0.000000          0   0   20  0.000000               0.0   
456255       71  0.070423          0   5   71  0.070423               0.0   

                                SK_ID_PREV NAME_CONTRACT_STATUS       
             max size      mean       size                 mean  sum  
SK_ID_CURR                                                            
100001       4.0    9  2.555556          9             7.222222   65  
100002      18.0   19  9.000000         19             7.000000  133  
100003      11.0   28  4.321429         28             7.071429  198  
100004       3.0    4  1.500000          4             7.250000   29  
100005       9.0   11  4.090909         11             7.000000   77  
...          ...  ...       ...        ...                  ...  ...  
456251       7.0    9  3.111111          9             7.000000   63  
456252       6.0    7  3.000000          7        

In [54]:
pos_cash_balance_agg.columns = pd.Index(['pos_cash_balance_'+e[0] + "_" + e[1].upper() for e in pos_cash_balance_agg.columns.tolist()]) 
pos_cash_balance_agg

pos_cash_balance_MONTHS_BALANCE_MIN  \
SK_ID_CURR                                        
100001                                      -96   
100002                                      -19   
100003                                      -77   
100004                                      -27   
100005                                      -25   
...                                         ...   
456251                                       -9   
456252                                      -82   
456253                                      -96   
456254                                      -11   
456255                                      -33   

            pos_cash_balance_MONTHS_BALANCE_MAX  \
SK_ID_CURR                                        
100001                                      -53   
100002                                       -1   
100003                                      -18   
100004                                      -24   
100005                                      -15   
...                                         ...   
456251                                       -1   
456252                                      -76   
456253                                      -57   
456254                                       -1   
456255                                       -2   

            pos_cash_balance_MONTHS_BALANCE_SIZE  \
SK_ID_CURR                                         
100001                                         9   
100002                                        19   
100003                                        28   
100004                                         4   
100005                                        11   
...                                          ...   
456251                                         9   
456252                                         7   
456253                                        17   
456254                                        20   
456255                                        71   

            pos_cash_balance_MONTHS_BALANCE_MEAN  \
SK_ID_CURR                                         
100001                                -72.555556   
100002                                -10.000000   
100003                                -43.785714   
100004                                -25.500000   
100005                                -20.000000   
...                                          ...   
456251                                 -5.000000   
456252                                -79.000000   
456253                                -79.235294   
456254                                 -5.550000   
456255                                -16.408451   

            pos_cash_balance_CNT_INSTALMENT_MIN  \
SK_ID_CURR                                        
100001                                      4.0   
100002                                     24.0   
100003                                      6.0   
100004                                      3.0   
100005                                      0.0   
...                                         ...   
456251                                      0.0   
456252                                      6.0   
456253                                      4.0   
456254                                     14.0   
456255                                      3.0   

            pos_cash_balance_CNT_INSTALMENT_MAX  \
SK_ID_CURR                                        
100001                                      4.0   
100002                                     24.0   
100003                                     12.0   
100004                                      4.0   
100005                                     12.0   
...                                         ...   
456251                                      8.0   
456252                                      6.0   
456253                                     12.0   
456254                                     16.0   
456255                                     36.0   

  

In [55]:
sk_id_prev_feature = [feature for feature in pos_cash_balance_agg.columns if 'SK_ID_PREV' in feature] 
sk_id_prev_feature

['pos_cash_balance_SK_ID_PREV_SIZE']

In [56]:
pos_cash_balance_agg.rename(columns = {'pos_cash_balance_SK_ID_PREV_SIZE':'pos_cash_balance_PREV_SIZE'}, inplace = True)

In [57]:
_, idx = np.unique(pos_cash_balance_agg, axis = 1, return_index = True)
pos_cash_balance_agg = pos_cash_balance_agg.iloc[:, idx]
pos_cash_balance_agg

pos_cash_balance_MONTHS_BALANCE_MIN  \
SK_ID_CURR                                        
100001                                      -96   
100002                                      -19   
100003                                      -77   
100004                                      -27   
100005                                      -25   
...                                         ...   
456251                                       -9   
456252                                      -82   
456253                                      -96   
456254                                      -11   
456255                                      -33   

            pos_cash_balance_MONTHS_BALANCE_MEAN  \
SK_ID_CURR                                         
100001                                -72.555556   
100002                                -10.000000   
100003                                -43.785714   
100004                                -25.500000   
100005                                -20.000000   
...                                          ...   
456251                                 -5.000000   
456252                                -79.000000   
456253                                -79.235294   
456254                                 -5.550000   
456255                                -16.408451   

            pos_cash_balance_MONTHS_BALANCE_MAX  \
SK_ID_CURR                                        
100001                                      -53   
100002                                       -1   
100003                                      -18   
100004                                      -24   
100005                                      -15   
...                                         ...   
456251                                       -1   
456252                                      -76   
456253                                      -57   
456254                                       -1   
456255                                       -2   

            pos_cash_balance_SK_DPD_DEF_MIN  pos_cash_balance_SK_DPD_MIN  \
SK_ID_CURR                                                                 
100001                                    0                            0   
100002                                    0                            0   
100003                                    0                            0   
100004                                    0                            0   
100005                                    0                            0   
...                                     ...                          ...   
456251                                    0                            0   
456252                                    0                            0   
456253                                    0                            0   
456254                                    0                            0   
456255                                    0                            0   

            pos_cash_balance_INSTALLMENTS_PAID_MIN  \
SK_ID_CURR                                           
100001                                         0.0   
100002                                         0.0   
100003                                         0.0   
100004                                         0.0   
100005                                         0.0   
...                                            ...   
456251                                         0.0   
456252                                         0.0   
456253                                         0.0   
456254                                         0.0   
456255                                         0.0   

            pos_cash_balance_CNT_INSTALMENT_FUTURE_MIN  \
SK_ID_CURR                                               
100001                                             0.0   
100002                                             6.0   
100003                                             0.0   
100004                   

Remove duplicate columns by values

In [58]:
pos_cash_balance_agg.isnull().sum().sum()

0

In [59]:
import gc
gc.enable()
del pos_cash_balance,pos_cash_balance_aggregations,sk_id_prev_feature
gc.collect()

0

## 4. Credit Card balance csv

In [61]:
credit_card_balance=pd.read_csv('credit_card_balance.csv')
credit_card_balance

SK_ID_PREV  SK_ID_CURR  MONTHS_BALANCE  AMT_BALANCE  \
0           2562384      378907              -6       56.970   
1           2582071      363914              -1    63975.555   
2           1740877      371185              -7    31815.225   
3           1389973      337855              -4   236572.110   
4           1891521      126868              -1   453919.455   
...             ...         ...             ...          ...   
3840307     1036507      328243              -9        0.000   
3840308     1714892      347207              -9        0.000   
3840309     1302323      215757              -9   275784.975   
3840310     1624872      430337             -10        0.000   
3840311     2411345      236760             -10        0.000   

         AMT_CREDIT_LIMIT_ACTUAL  AMT_DRAWINGS_ATM_CURRENT  \
0                         135000                       0.0   
1                          45000                    2250.0   
2                         450000                       0.0   
3                         225000                    2250.0   
4                         450000                       0.0   
...                          ...                       ...   
3840307                    45000                       NaN   
3840308                    45000                       0.0   
3840309                   585000                  270000.0   
3840310                   450000                       NaN   
3840311                   157500                       0.0   

         AMT_DRAWINGS_CURRENT  AMT_DRAWINGS_OTHER_CURRENT  \
0                       877.5                         0.0   
1                      2250.0                         0.0   
2                         0.0                         0.0   
3                      2250.0                         0.0   
4                     11547.0                         0.0   
...                       ...                         ...   
3840307                   0.0                         NaN   
3840308                   0.0                         0.0   
3840309              270000.0                         0.0   
3840310                   0.0                         NaN   
3840311                   0.0                         0.0   

         AMT_DRAWINGS_POS_CURRENT  AMT_INST_MIN_REGULARITY  \
0                           877.5                 1700.325   
1                             0.0                 2250.000   
2                             0.0                 2250.000   
3                             0.0                11795.760   
4                         11547.0                22924.890   
...                           ...                      ...   
3840307                       NaN                    0.000   
3840308                       0.0                    0.000   
3840309                       0.0                 2250.000   
3840310                       NaN                    0.000   
3840311                       0.0                    0.000   

         AMT_PAYMENT_CURRENT  AMT_PAYMENT_TOTAL_CURRENT  \
0                    1800.00                   1800.000   
1                    2250.00                   2250.000   
2                    2250.00                   2250.000   
3                   11925.00                  11925.000   
4                   27000.00                  27000.000   
...                      ...                        ...   
3840307                  NaN                      0.000   
3840308              1879.11                      0.000   
3840309            375750.00                 356994.675   
3840310                  NaN                      0.000   
3840311                 0.00                      0.000   

         AMT_RECEIVABLE_PRINCIPAL  AMT_RECIVABLE  AMT_TOTAL_RECEIVABLE  \
0                           0.000          0.000                 0.000   
1                       60175.080      64875.555             64875.555   
2                       26926.425      31460.085             31460.085   
3           

In [62]:
credit_card_balance.dtypes

SK_ID_PREV                      int64
SK_ID_CURR                      int64
MONTHS_BALANCE                  int64
AMT_BALANCE                   float64
AMT_CREDIT_LIMIT_ACTUAL         int64
AMT_DRAWINGS_ATM_CURRENT      float64
AMT_DRAWINGS_CURRENT          float64
AMT_DRAWINGS_OTHER_CURRENT    float64
AMT_DRAWINGS_POS_CURRENT      float64
AMT_INST_MIN_REGULARITY       float64
AMT_PAYMENT_CURRENT           float64
AMT_PAYMENT_TOTAL_CURRENT     float64
AMT_RECEIVABLE_PRINCIPAL      float64
AMT_RECIVABLE                 float64
AMT_TOTAL_RECEIVABLE          float64
CNT_DRAWINGS_ATM_CURRENT      float64
CNT_DRAWINGS_CURRENT            int64
CNT_DRAWINGS_OTHER_CURRENT    float64
CNT_DRAWINGS_POS_CURRENT      float64
CNT_INSTALMENT_MATURE_CUM     float64
NAME_CONTRACT_STATUS           object
SK_DPD                          int64
SK_DPD_DEF                      int64
dtype: object

## Determining correlation 

In [64]:
threshold = 0.9

corr_matrix = credit_card_balance.select_dtypes(include=['float64', 'int64']).corr().abs()
corr_matrix.head()

SK_ID_PREV  SK_ID_CURR  MONTHS_BALANCE  AMT_BALANCE  \
SK_ID_PREV                 1.000000    0.004723        0.003670     0.005046   
SK_ID_CURR                 0.004723    1.000000        0.001696     0.003510   
MONTHS_BALANCE             0.003670    0.001696        1.000000     0.014558   
AMT_BALANCE                0.005046    0.003510        0.014558     1.000000   
AMT_CREDIT_LIMIT_ACTUAL    0.006631    0.005991        0.199900     0.489386   

                         AMT_CREDIT_LIMIT_ACTUAL  AMT_DRAWINGS_ATM_CURRENT  \
SK_ID_PREV                              0.006631                  0.004342   
SK_ID_CURR                              0.005991                  0.000814   
MONTHS_BALANCE                          0.199900                  0.036802   
AMT_BALANCE                             0.489386                  0.283551   
AMT_CREDIT_LIMIT_ACTUAL                 1.000000                  0.247219   

                         AMT_DRAWINGS_CURRENT  AMT_DRAWINGS_OTHER_CURRENT  \
SK_ID_PREV                           0.002624                    0.000160   
SK_ID_CURR                           0.000708                    0.000958   
MONTHS_BALANCE                       0.065527                    0.000405   
AMT_BALANCE                          0.336965                    0.065366   
AMT_CREDIT_LIMIT_ACTUAL              0.263093                    0.050579   

                         AMT_DRAWINGS_POS_CURRENT  AMT_INST_MIN_REGULARITY  \
SK_ID_PREV                               0.001721                 0.006460   
SK_ID_CURR                               0.000786                 0.003300   
MONTHS_BALANCE                           0.118146                 0.087529   
AMT_BALANCE                              0.169449                 0.896728   
AMT_CREDIT_LIMIT_ACTUAL                  0.234976                 0.467620   

                         AMT_PAYMENT_CURRENT  AMT_PAYMENT_TOTAL_CURRENT  \
SK_ID_PREV                          0.003472                   0.001641   
SK_ID_CURR                          0.000127                   0.000784   
MONTHS_BALANCE                      0.076355                   0.035614   
AMT_BALANCE                         0.143934                   0.151349   
AMT_CREDIT_LIMIT_ACTUAL             0.308294                   0.226570   

                         AMT_RECEIVABLE_PRINCIPAL  AMT_RECIVABLE  \
SK_ID_PREV                               0.005140       0.005035   
SK_ID_CURR                               0.003589       0.003518   
MONTHS_BALANCE                           0.016266       0.013172   
AMT_BALANCE                              0.999720       0.999917   
AMT_CREDIT_LIMIT_ACTUAL                  0.490445       0.488641   

                         AMT_TOTAL_RECEIVABLE  CNT_DRAWINGS_ATM_CURRENT  \
SK_ID_PREV                           0.005032                  0.002821   
SK_ID_CURR                           0.003524                  0.002082   
MONTHS_BALANCE                       0.013084                  0.002536   
AMT_BALANCE                          0.999897                  0.309968   
AMT_CREDIT_LIMIT_ACTUAL              0.488598                  0.221808   

                         CNT_DRAWINGS_CURRENT  CNT_DRAWINGS_OTHER_CURRENT  \
SK_ID_PREV                           0.000367                    0.001412   
SK_ID_CURR                           0.002654                    0.000131   
MONTHS_BALANCE                       0.113321                    0.026192   
AMT_BALANCE                          0.259184                    0.046563   
AMT_CREDIT_LIMIT_ACTUAL              0.204237                    0.030051   

                         CNT_DRAWINGS_POS_CURRENT  CNT_INSTALMENT_MATURE_CUM  \
SK_ID_PREV                               0.000809                   0.007219   
SK_ID_CURR                               0.002135                   0.000581   
MONTHS_BALANCE                           0.160207                   0.008620   
AMT_BALANCE                              0.155553

In [65]:
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))
upper.head()

SK_ID_PREV  SK_ID_CURR  MONTHS_BALANCE  AMT_BALANCE  \
SK_ID_PREV                      NaN    0.004723        0.003670     0.005046   
SK_ID_CURR                      NaN         NaN        0.001696     0.003510   
MONTHS_BALANCE                  NaN         NaN             NaN     0.014558   
AMT_BALANCE                     NaN         NaN             NaN          NaN   
AMT_CREDIT_LIMIT_ACTUAL         NaN         NaN             NaN          NaN   

                         AMT_CREDIT_LIMIT_ACTUAL  AMT_DRAWINGS_ATM_CURRENT  \
SK_ID_PREV                              0.006631                  0.004342   
SK_ID_CURR                              0.005991                  0.000814   
MONTHS_BALANCE                          0.199900                  0.036802   
AMT_BALANCE                             0.489386                  0.283551   
AMT_CREDIT_LIMIT_ACTUAL                      NaN                  0.247219   

                         AMT_DRAWINGS_CURRENT  AMT_DRAWINGS_OTHER_CURRENT  \
SK_ID_PREV                           0.002624                    0.000160   
SK_ID_CURR                           0.000708                    0.000958   
MONTHS_BALANCE                       0.065527                    0.000405   
AMT_BALANCE                          0.336965                    0.065366   
AMT_CREDIT_LIMIT_ACTUAL              0.263093                    0.050579   

                         AMT_DRAWINGS_POS_CURRENT  AMT_INST_MIN_REGULARITY  \
SK_ID_PREV                               0.001721                 0.006460   
SK_ID_CURR                               0.000786                 0.003300   
MONTHS_BALANCE                           0.118146                 0.087529   
AMT_BALANCE                              0.169449                 0.896728   
AMT_CREDIT_LIMIT_ACTUAL                  0.234976                 0.467620   

                         AMT_PAYMENT_CURRENT  AMT_PAYMENT_TOTAL_CURRENT  \
SK_ID_PREV                          0.003472                   0.001641   
SK_ID_CURR                          0.000127                   0.000784   
MONTHS_BALANCE                      0.076355                   0.035614   
AMT_BALANCE                         0.143934                   0.151349   
AMT_CREDIT_LIMIT_ACTUAL             0.308294                   0.226570   

                         AMT_RECEIVABLE_PRINCIPAL  AMT_RECIVABLE  \
SK_ID_PREV                               0.005140       0.005035   
SK_ID_CURR                               0.003589       0.003518   
MONTHS_BALANCE                           0.016266       0.013172   
AMT_BALANCE                              0.999720       0.999917   
AMT_CREDIT_LIMIT_ACTUAL                  0.490445       0.488641   

                         AMT_TOTAL_RECEIVABLE  CNT_DRAWINGS_ATM_CURRENT  \
SK_ID_PREV                           0.005032                  0.002821   
SK_ID_CURR                           0.003524                  0.002082   
MONTHS_BALANCE                       0.013084                  0.002536   
AMT_BALANCE                          0.999897                  0.309968   
AMT_CREDIT_LIMIT_ACTUAL              0.488598                  0.221808   

                         CNT_DRAWINGS_CURRENT  CNT_DRAWINGS_OTHER_CURRENT  \
SK_ID_PREV                           0.000367                    0.001412   
SK_ID_CURR                           0.002654                    0.000131   
MONTHS_BALANCE                       0.113321                    0.026192   
AMT_BALANCE                          0.259184                    0.046563   
AMT_CREDIT_LIMIT_ACTUAL              0.204237                    0.030051   

                         CNT_DRAWINGS_POS_CURRENT  CNT_INSTALMENT_MATURE_CUM  \
SK_ID_PREV                               0.000809                   0.007219   
SK_ID_CURR                               0.002135                   0.000581   
MONTHS_BALANCE                           0.160207                   0.008620   
AMT_BALANCE                              0.155553

extracting the upper triangle of the correlation matrix (corr_matrix), excluding the diagonal, using np.triu(). The where function keeps only the values above the diagonal (setting others to NaN). The result is stored in upper, which shows the upper triangular portion of the correlation matrix for easier inspection of correlations between variables.

In [66]:
# Select columns with correlations above threshold
to_drop = [column for column in upper.columns if any(upper[column] > threshold)]

print('There are %d columns to remove.' % (len(to_drop)))

There are 5 columns to remove.


In [67]:
to_drop

['AMT_PAYMENT_TOTAL_CURRENT',
 'AMT_RECEIVABLE_PRINCIPAL',
 'AMT_RECIVABLE',
 'AMT_TOTAL_RECEIVABLE',
 'CNT_DRAWINGS_POS_CURRENT']

In [68]:
credit_card_balance = credit_card_balance.drop(columns = to_drop)

## Encoding

In [70]:
credit_card_balance.NAME_CONTRACT_STATUS=credit_card_balance.NAME_CONTRACT_STATUS.map({'Completed':6,'Active':5,'Signed':4,'Approved':3,'Refused':2,'Sent proposal':1,'Demand':0})

In [71]:
credit_card_balance

SK_ID_PREV  SK_ID_CURR  MONTHS_BALANCE  AMT_BALANCE  \
0           2562384      378907              -6       56.970   
1           2582071      363914              -1    63975.555   
2           1740877      371185              -7    31815.225   
3           1389973      337855              -4   236572.110   
4           1891521      126868              -1   453919.455   
...             ...         ...             ...          ...   
3840307     1036507      328243              -9        0.000   
3840308     1714892      347207              -9        0.000   
3840309     1302323      215757              -9   275784.975   
3840310     1624872      430337             -10        0.000   
3840311     2411345      236760             -10        0.000   

         AMT_CREDIT_LIMIT_ACTUAL  AMT_DRAWINGS_ATM_CURRENT  \
0                         135000                       0.0   
1                          45000                    2250.0   
2                         450000                       0.0   
3                         225000                    2250.0   
4                         450000                       0.0   
...                          ...                       ...   
3840307                    45000                       NaN   
3840308                    45000                       0.0   
3840309                   585000                  270000.0   
3840310                   450000                       NaN   
3840311                   157500                       0.0   

         AMT_DRAWINGS_CURRENT  AMT_DRAWINGS_OTHER_CURRENT  \
0                       877.5                         0.0   
1                      2250.0                         0.0   
2                         0.0                         0.0   
3                      2250.0                         0.0   
4                     11547.0                         0.0   
...                       ...                         ...   
3840307                   0.0                         NaN   
3840308                   0.0                         0.0   
3840309              270000.0                         0.0   
3840310                   0.0                         NaN   
3840311                   0.0                         0.0   

         AMT_DRAWINGS_POS_CURRENT  AMT_INST_MIN_REGULARITY  \
0                           877.5                 1700.325   
1                             0.0                 2250.000   
2                             0.0                 2250.000   
3                             0.0                11795.760   
4                         11547.0                22924.890   
...                           ...                      ...   
3840307                       NaN                    0.000   
3840308                       0.0                    0.000   
3840309                       0.0                 2250.000   
3840310                       NaN                    0.000   
3840311                       0.0                    0.000   

         AMT_PAYMENT_CURRENT  CNT_DRAWINGS_ATM_CURRENT  CNT_DRAWINGS_CURRENT  \
0                    1800.00                       0.0                     1   
1                    2250.00                       1.0                     1   
2                    2250.00                       0.0                     0   
3                   11925.00                       1.0                     1   
4                   27000.00                       0.0                     1   
...                      ...                       ...                   ...   
3840307                  NaN                       NaN                     0   
3840308              1879.11                       0.0                     0   
3840309            375750.00                       2.0                     2   
3840310                  NaN                       NaN                     0   
3840311                 0.00                       0.0                     0   

         CNT_DRAWINGS_OTHER_CURRENT  CNT_INSTALMENT_MATU

## Outliers handling

In [73]:
credit_card_balance.loc[(credit_card_balance.CNT_DRAWINGS_CURRENT>150),'CNT_DRAWINGS_CURRENT']=np.median(credit_card_balance.CNT_DRAWINGS_CURRENT)
credit_card_balance.loc[(credit_card_balance.CNT_DRAWINGS_ATM_CURRENT>50),'CNT_DRAWINGS_ATM_CURRENT']=np.median(credit_card_balance.CNT_DRAWINGS_ATM_CURRENT)
credit_card_balance.loc[(credit_card_balance.AMT_PAYMENT_CURRENT>4000000),'AMT_PAYMENT_CURRENT']=np.median(credit_card_balance.AMT_PAYMENT_CURRENT)
credit_card_balance.loc[(credit_card_balance.AMT_INST_MIN_REGULARITY>150000),'AMT_INST_MIN_REGULARITY']=np.median(credit_card_balance.AMT_INST_MIN_REGULARITY)
credit_card_balance.loc[(credit_card_balance.AMT_DRAWINGS_POS_CURRENT>2000000),'AMT_DRAWINGS_POS_CURRENT']=np.median(credit_card_balance.AMT_DRAWINGS_POS_CURRENT)
credit_card_balance.loc[(credit_card_balance.AMT_DRAWINGS_OTHER_CURRENT>1200000),'AMT_DRAWINGS_OTHER_CURRENT']=np.median(credit_card_balance.AMT_DRAWINGS_OTHER_CURRENT)
credit_card_balance.loc[(credit_card_balance.AMT_DRAWINGS_ATM_CURRENT>2000000),'AMT_DRAWINGS_ATM_CURRENT']=np.median(credit_card_balance.AMT_DRAWINGS_ATM_CURRENT)
credit_card_balance.loc[(credit_card_balance.AMT_DRAWINGS_CURRENT>2000000),'AMT_DRAWINGS_CURRENT']=np.median(credit_card_balance.AMT_DRAWINGS_CURRENT)
credit_card_balance.loc[(credit_card_balance.AMT_CREDIT_LIMIT_ACTUAL>1000000),'AMT_CREDIT_LIMIT_ACTUAL']=np.median(credit_card_balance.AMT_CREDIT_LIMIT_ACTUAL)
credit_card_balance.loc[(credit_card_balance.AMT_BALANCE>1500000),'AMT_BALANCE']=np.median(credit_card_balance.AMT_BALANCE)

## Handling missing values

In [75]:
credit_card_balance_features_with_na=[features for features in credit_card_balance.columns if credit_card_balance[features].isnull().sum()>0] 
print('The Features that have missing values are as follows: \n',credit_card_balance_features_with_na)
print('The number of Features with missing values are:',len(credit_card_balance_features_with_na))

The Features that have missing values are as follows: 
 ['AMT_DRAWINGS_ATM_CURRENT', 'AMT_DRAWINGS_OTHER_CURRENT', 'AMT_DRAWINGS_POS_CURRENT', 'AMT_INST_MIN_REGULARITY', 'AMT_PAYMENT_CURRENT', 'CNT_DRAWINGS_ATM_CURRENT', 'CNT_DRAWINGS_OTHER_CURRENT', 'CNT_INSTALMENT_MATURE_CUM']
The number of Features with missing values are: 8


In [76]:
credit_card_balance['CNT_DRAWINGS_OTHER_CURRENT'] = credit_card_balance['CNT_DRAWINGS_OTHER_CURRENT'].fillna(0)
credit_card_balance['CNT_DRAWINGS_ATM_CURRENT'] = credit_card_balance['CNT_DRAWINGS_ATM_CURRENT'].fillna(0)
credit_card_balance['CNT_INSTALMENT_MATURE_CUM'] = credit_card_balance['CNT_INSTALMENT_MATURE_CUM'].fillna(0)
credit_card_balance['AMT_PAYMENT_CURRENT'] = credit_card_balance['AMT_PAYMENT_CURRENT'].fillna(credit_card_balance['AMT_PAYMENT_CURRENT'].median())
credit_card_balance['AMT_DRAWINGS_ATM_CURRENT'] = credit_card_balance['AMT_DRAWINGS_ATM_CURRENT'].fillna(credit_card_balance['AMT_DRAWINGS_ATM_CURRENT'].median())
credit_card_balance['AMT_DRAWINGS_OTHER_CURRENT'] = credit_card_balance['AMT_DRAWINGS_OTHER_CURRENT'].fillna(credit_card_balance['AMT_DRAWINGS_OTHER_CURRENT'].median())
credit_card_balance['AMT_DRAWINGS_POS_CURRENT'] = credit_card_balance['AMT_DRAWINGS_POS_CURRENT'].fillna(credit_card_balance['AMT_DRAWINGS_POS_CURRENT'].median())
credit_card_balance['AMT_INST_MIN_REGULARITY'] = credit_card_balance['AMT_INST_MIN_REGULARITY'].fillna(credit_card_balance['AMT_INST_MIN_REGULARITY'].median())

In [77]:
credit_card_balance.isnull().sum().sum()

0

In [78]:
credit_card_balance.columns

Index(['SK_ID_PREV', 'SK_ID_CURR', 'MONTHS_BALANCE', 'AMT_BALANCE',
       'AMT_CREDIT_LIMIT_ACTUAL', 'AMT_DRAWINGS_ATM_CURRENT',
       'AMT_DRAWINGS_CURRENT', 'AMT_DRAWINGS_OTHER_CURRENT',
       'AMT_DRAWINGS_POS_CURRENT', 'AMT_INST_MIN_REGULARITY',
       'AMT_PAYMENT_CURRENT', 'CNT_DRAWINGS_ATM_CURRENT',
       'CNT_DRAWINGS_CURRENT', 'CNT_DRAWINGS_OTHER_CURRENT',
       'CNT_INSTALMENT_MATURE_CUM', 'NAME_CONTRACT_STATUS', 'SK_DPD',
       'SK_DPD_DEF'],
      dtype='object')

## Aggregations

In [80]:
credit_card_balance_aggregations = {'MONTHS_BALANCE': ['min', 'max', 'size','mean'],
                                    'AMT_BALANCE': ['min', 'max', 'size','mean'],
                                    'AMT_CREDIT_LIMIT_ACTUAL': ['min', 'max', 'size','mean'], 'AMT_DRAWINGS_ATM_CURRENT': ['min', 'max', 'size','mean'],
                                    'AMT_DRAWINGS_CURRENT': ['min', 'max', 'size','mean'], 'AMT_DRAWINGS_OTHER_CURRENT': ['min', 'max', 'size','mean'],
                                    'AMT_DRAWINGS_POS_CURRENT': ['min', 'max', 'size','mean'], 'AMT_INST_MIN_REGULARITY': ['min', 'max', 'size','mean'],
                                    'AMT_PAYMENT_CURRENT': ['min', 'max', 'size','mean'], 'CNT_DRAWINGS_ATM_CURRENT': ['min', 'max', 'size','mean'],
                                    'CNT_DRAWINGS_CURRENT': ['min', 'max', 'size','mean'], 'CNT_DRAWINGS_OTHER_CURRENT': ['min', 'max', 'size','mean'],
                                    'CNT_INSTALMENT_MATURE_CUM': ['min', 'max', 'size','mean'], 'SK_DPD': ['min', 'max', 'size','mean'],
                                    'SK_DPD_DEF': ['min', 'max', 'size','mean'],
                                    'SK_ID_PREV': ['size'], 
                                    'NAME_CONTRACT_STATUS':['mean','sum']}
credit_card_balance_agg = credit_card_balance.groupby('SK_ID_CURR').agg(credit_card_balance_aggregations) 
credit_card_balance_agg

MONTHS_BALANCE                AMT_BALANCE                   \
                      min max size  mean         min         max size   
SK_ID_CURR                                                              
100006                 -6  -1    6  -3.5       0.000       0.000    6   
100011                -75  -2   74 -38.5       0.000  189000.000   74   
100013                -96  -1   96 -48.5       0.000  161420.220   96   
100021                -18  -2   17 -10.0       0.000       0.000   17   
100023                -11  -4    8  -7.5       0.000       0.000    8   
...                   ...  ..  ...   ...         ...         ...  ...   
456244                -41  -1   41 -21.0       0.000  453627.675   41   
456246                 -9  -2    8  -5.5       0.000   43490.115    8   
456247                -96  -2   95 -49.0       0.000  190202.130   95   
456248                -24  -2   23 -13.0       0.000       0.000   23   
456250                -12  -1   12  -6.5  153832.725  200208.915   12   

                          AMT_CREDIT_LIMIT_ACTUAL                              \
                     mean                     min     max size           mean   
SK_ID_CURR                                                                      
100006           0.000000                  270000  270000    6  270000.000000   
100011       54482.111149                   90000  180000   74  164189.189189   
100013       18159.919219                   45000  157500   96  131718.750000   
100021           0.000000                  675000  675000   17  675000.000000   
100023           0.000000                   45000  225000    8  135000.000000   
...                   ...                     ...     ...  ...            ...   
456244      131834.730732                       0  450000   41  296341.463415   
456246       13136.731875                  135000  135000    8  135000.000000   
456247       23216.396211                       0  180000   95  144000.000000   
456248           0.000000                  900000  900000   23  900000.000000   
456250      173589.326250                  175500  180000   12  178875.000000   

           AMT_DRAWINGS_ATM_CURRENT                               \
                                min       max size          mean   
SK_ID_CURR                                                         
100006                          0.0       0.0    6      0.000000   
100011                          0.0  180000.0   74   2432.432432   
100013                          0.0  157500.0   96   5953.125000   
100021                          0.0       0.0   17      0.000000   
100023                          0.0       0.0    8      0.000000   
...                             ...       ...  ...           ...   
456244                          0.0  279000.0   41  24475.609756   
456246                          0.0       0.0    8      0.000000   
456247                          0.0   96750.0   95   2136.315789   
456248                          0.0       0.0   23      0.000000   
456250                          0.0  171000.0   12  15000.000000   

           AMT_DRAWINGS_CURRENT                                \
                            min        max size          mean   
SK_ID_CURR                                                      
100006                      0.0       0.00    6      0.000000   
100011                      0.0  180000.00   74   2432.432432   
100013                      0.0  157500.00   96   5953.125000   
100021                      0.0       0.00   17      0.000000   
100023                      0.0       0.00    8      0.000000   
...                         ...        ...  ...           ...   
456244                      0.0  307953.45   41  26842.388049   
456246                      0.0   48929.85    8  15199.256250   
456247                      0.0   96750.00   95   2149.506474   
456248                      0.0       0.00   23      0.000000   
456250                      0.0  171000.00   12  15000.

In [81]:
credit_card_balance_agg.columns = pd.Index(['credit_card_balance_'+e[0] + "_" + e[1].upper() for e in credit_card_balance_agg.columns.tolist()]) 
credit_card_balance_agg

credit_card_balance_MONTHS_BALANCE_MIN  \
SK_ID_CURR                                           
100006                                          -6   
100011                                         -75   
100013                                         -96   
100021                                         -18   
100023                                         -11   
...                                            ...   
456244                                         -41   
456246                                          -9   
456247                                         -96   
456248                                         -24   
456250                                         -12   

            credit_card_balance_MONTHS_BALANCE_MAX  \
SK_ID_CURR                                           
100006                                          -1   
100011                                          -2   
100013                                          -1   
100021                                          -2   
100023                                          -4   
...                                            ...   
456244                                          -1   
456246                                          -2   
456247                                          -2   
456248                                          -2   
456250                                          -1   

            credit_card_balance_MONTHS_BALANCE_SIZE  \
SK_ID_CURR                                            
100006                                            6   
100011                                           74   
100013                                           96   
100021                                           17   
100023                                            8   
...                                             ...   
456244                                           41   
456246                                            8   
456247                                           95   
456248                                           23   
456250                                           12   

            credit_card_balance_MONTHS_BALANCE_MEAN  \
SK_ID_CURR                                            
100006                                         -3.5   
100011                                        -38.5   
100013                                        -48.5   
100021                                        -10.0   
100023                                         -7.5   
...                                             ...   
456244                                        -21.0   
456246                                         -5.5   
456247                                        -49.0   
456248                                        -13.0   
456250                                         -6.5   

            credit_card_balance_AMT_BALANCE_MIN  \
SK_ID_CURR                                        
100006                                    0.000   
100011                                    0.000   
100013                                    0.000   
100021                                    0.000   
100023                                    0.000   
...                                         ...   
456244                                    0.000   
456246                                    0.000   
456247                                    0.000   
456248                                    0.000   
456250                               153832.725   

            credit_card_balance_AMT_BALANCE_MAX  \
SK_ID_CURR                                        
100006                                    0.000   
100011                               189000.000   
100013                               161420.220   
100021                                    0.000   
100023                                    0.000   
...                                         ...   
456244                               453627.675   
456246                                43490.115   


In [82]:
sk_id_prev_feature = [feature for feature in credit_card_balance_agg.columns if 'SK_ID_PREV' in feature] 
sk_id_prev_feature

['credit_card_balance_SK_ID_PREV_SIZE']

In [83]:
credit_card_balance_agg.rename(columns = {'credit_card_balance_SK_ID_PREV_SIZE':'credit_card_balance_PREV_SIZE'}, inplace = True)

In [84]:
_, idx = np.unique(credit_card_balance_agg, axis = 1, return_index = True)
credit_card_balance_agg = credit_card_balance_agg.iloc[:, idx]
credit_card_balance_agg

credit_card_balance_MONTHS_BALANCE_MIN  \
SK_ID_CURR                                           
100006                                          -6   
100011                                         -75   
100013                                         -96   
100021                                         -18   
100023                                         -11   
...                                            ...   
456244                                         -41   
456246                                          -9   
456247                                         -96   
456248                                         -24   
456250                                         -12   

            credit_card_balance_MONTHS_BALANCE_MEAN  \
SK_ID_CURR                                            
100006                                         -3.5   
100011                                        -38.5   
100013                                        -48.5   
100021                                        -10.0   
100023                                         -7.5   
...                                             ...   
456244                                        -21.0   
456246                                         -5.5   
456247                                        -49.0   
456248                                        -13.0   
456250                                         -6.5   

            credit_card_balance_MONTHS_BALANCE_MAX  \
SK_ID_CURR                                           
100006                                          -1   
100011                                          -2   
100013                                          -1   
100021                                          -2   
100023                                          -4   
...                                            ...   
456244                                          -1   
456246                                          -2   
456247                                          -2   
456248                                          -2   
456250                                          -1   

            credit_card_balance_SK_DPD_MIN  \
SK_ID_CURR                                   
100006                                   0   
100011                                   0   
100013                                   0   
100021                                   0   
100023                                   0   
...                                    ...   
456244                                   0   
456246                                   0   
456247                                   0   
456248                                   0   
456250                                   0   

            credit_card_balance_CNT_DRAWINGS_OTHER_CURRENT_MIN  \
SK_ID_CURR                                                       
100006                                                    0.0    
100011                                                    0.0    
100013                                                    0.0    
100021                                                    0.0    
100023                                                    0.0    
...                                                       ...    
456244                                                    0.0    
456246                                                    0.0    
456247                                                    0.0    
456248                                                    0.0    
456250                                                    0.0    

            credit_card_balance_AMT_DRAWINGS_OTHER_CURRENT_MIN  \
SK_ID_CURR                                                       
100006                                                    0.0    
100011                                                    0.0    
100013                                                    0.0    
100021                                                    0.0    
100023                              

Removing duplicate columns based on values

In [85]:
credit_card_balance_agg.std()

credit_card_balance_MONTHS_BALANCE_MIN                     33.379821
credit_card_balance_MONTHS_BALANCE_MEAN                    16.666571
credit_card_balance_MONTHS_BALANCE_MAX                      0.734817
credit_card_balance_SK_DPD_MIN                              1.423225
credit_card_balance_CNT_DRAWINGS_OTHER_CURRENT_MIN          0.005382
credit_card_balance_AMT_DRAWINGS_OTHER_CURRENT_MIN        448.600819
credit_card_balance_AMT_DRAWINGS_POS_CURRENT_MIN         4484.987951
credit_card_balance_AMT_INST_MIN_REGULARITY_MIN           295.140969
credit_card_balance_CNT_INSTALMENT_MATURE_CUM_MIN           2.481125
credit_card_balance_CNT_DRAWINGS_ATM_CURRENT_MIN            0.254408
credit_card_balance_CNT_DRAWINGS_CURRENT_MIN                0.981504
credit_card_balance_AMT_DRAWINGS_ATM_CURRENT_MIN         6080.483893
credit_card_balance_AMT_DRAWINGS_CURRENT_MIN             8737.335013
credit_card_balance_AMT_BALANCE_MIN                     44311.662362
credit_card_balance_CNT_DRAWINGS_O

In [86]:
credit_card_balance_agg.isnull().sum().sum()

0

## Garbage collection

In [88]:
## to optimize memory 
gc.enable()
del credit_card_balance,corr_matrix,upper,to_drop,credit_card_balance_aggregations,sk_id_prev_feature
gc.collect()

0

## 5. Installments_payments csv

In [90]:
installments_payments = pd.read_csv('installments_payments.csv')
installments_payments

SK_ID_PREV  SK_ID_CURR  NUM_INSTALMENT_VERSION  \
0            1054186      161674                     1.0   
1            1330831      151639                     0.0   
2            2085231      193053                     2.0   
3            2452527      199697                     1.0   
4            2714724      167756                     1.0   
...              ...         ...                     ...   
13605396     2186857      428057                     0.0   
13605397     1310347      414406                     0.0   
13605398     1308766      402199                     0.0   
13605399     1062206      409297                     0.0   
13605400     2448869      434321                     1.0   

          NUM_INSTALMENT_NUMBER  DAYS_INSTALMENT  DAYS_ENTRY_PAYMENT  \
0                             6          -1180.0             -1187.0   
1                            34          -2156.0             -2156.0   
2                             1            -63.0               -63.0   
3                             3          -2418.0             -2426.0   
4                             2          -1383.0             -1366.0   
...                         ...              ...                 ...   
13605396                     66          -1624.0                 NaN   
13605397                     47          -1539.0                 NaN   
13605398                     43             -7.0                 NaN   
13605399                     43          -1986.0                 NaN   
13605400                     19            -27.0                 NaN   

          AMT_INSTALMENT  AMT_PAYMENT  
0               6948.360     6948.360  
1               1716.525     1716.525  
2              25425.000    25425.000  
3              24350.130    24350.130  
4               2165.040     2160.585  
...                  ...          ...  
13605396          67.500          NaN  
13605397          67.500          NaN  
13605398       43737.435          NaN  
13605399          67.500          NaN  
13605400       11504.250          NaN  

[13605401 rows x 8 columns]

## Correlation

In [92]:
threshold = 0.9

# Absolute value correlation matrix
corr_matrix = installments_payments.corr().abs()
corr_matrix.head()

SK_ID_PREV  SK_ID_CURR  NUM_INSTALMENT_VERSION  \
SK_ID_PREV                1.000000    0.002132                0.000685   
SK_ID_CURR                0.002132    1.000000                0.000480   
NUM_INSTALMENT_VERSION    0.000685    0.000480                1.000000   
NUM_INSTALMENT_NUMBER     0.002095    0.000548                0.323414   
DAYS_INSTALMENT           0.003748    0.001191                0.130244   

                        NUM_INSTALMENT_NUMBER  DAYS_INSTALMENT  \
SK_ID_PREV                           0.002095         0.003748   
SK_ID_CURR                           0.000548         0.001191   
NUM_INSTALMENT_VERSION               0.323414         0.130244   
NUM_INSTALMENT_NUMBER                1.000000         0.090286   
DAYS_INSTALMENT                      0.090286         1.000000   

                        DAYS_ENTRY_PAYMENT  AMT_INSTALMENT  AMT_PAYMENT  
SK_ID_PREV                        0.003734        0.002042     0.001887  
SK_ID_CURR                        0.001215        0.000226     0.000124  
NUM_INSTALMENT_VERSION            0.128124        0.168109     0.177176  
NUM_INSTALMENT_NUMBER             0.094305        0.089640     0.087664  
DAYS_INSTALMENT                   0.999491        0.125985     0.127018

 showing how each feature correlates with others, only representing positive values

In [93]:
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))
upper.head()

SK_ID_PREV  SK_ID_CURR  NUM_INSTALMENT_VERSION  \
SK_ID_PREV                     NaN    0.002132                0.000685   
SK_ID_CURR                     NaN         NaN                0.000480   
NUM_INSTALMENT_VERSION         NaN         NaN                     NaN   
NUM_INSTALMENT_NUMBER          NaN         NaN                     NaN   
DAYS_INSTALMENT                NaN         NaN                     NaN   

                        NUM_INSTALMENT_NUMBER  DAYS_INSTALMENT  \
SK_ID_PREV                           0.002095         0.003748   
SK_ID_CURR                           0.000548         0.001191   
NUM_INSTALMENT_VERSION               0.323414         0.130244   
NUM_INSTALMENT_NUMBER                     NaN         0.090286   
DAYS_INSTALMENT                           NaN              NaN   

                        DAYS_ENTRY_PAYMENT  AMT_INSTALMENT  AMT_PAYMENT  
SK_ID_PREV                        0.003734        0.002042     0.001887  
SK_ID_CURR                        0.001215        0.000226     0.000124  
NUM_INSTALMENT_VERSION            0.128124        0.168109     0.177176  
NUM_INSTALMENT_NUMBER             0.094305        0.089640     0.087664  
DAYS_INSTALMENT                   0.999491        0.125985     0.127018

In [94]:
to_drop = [column for column in upper.columns if any(upper[column] > threshold)]

print('There are %d columns to remove.' % (len(to_drop)))

There are 2 columns to remove.


In [95]:
to_drop

['DAYS_ENTRY_PAYMENT', 'AMT_PAYMENT']

In [96]:
installments_payments = installments_payments.drop(columns = to_drop)

## Outlier handling

In [98]:
installments_payments.loc[(installments_payments.NUM_INSTALMENT_VERSION>150),'NUM_INSTALMENT_VERSION']=np.median(installments_payments.NUM_INSTALMENT_VERSION)
installments_payments.loc[(installments_payments.AMT_INSTALMENT>3000000),'AMT_INSTALMENT']=np.median(installments_payments.AMT_INSTALMENT)

## Missing Values

In [100]:
installments_payments_features_with_na=[features for features in installments_payments.columns if installments_payments[features].isnull().sum()>0] 
print('The Features that have missing values are as follows: \n',installments_payments_features_with_na)
print('The number of Features with missing values are:',len(installments_payments_features_with_na))

The Features that have missing values are as follows: 
 []
The number of Features with missing values are: 0


In [101]:
installments_payments.columns

Index(['SK_ID_PREV', 'SK_ID_CURR', 'NUM_INSTALMENT_VERSION',
       'NUM_INSTALMENT_NUMBER', 'DAYS_INSTALMENT', 'AMT_INSTALMENT'],
      dtype='object')

In [102]:
installments_payments_aggregations = {'NUM_INSTALMENT_VERSION': ['min', 'max', 'size','mean'],
                                    'NUM_INSTALMENT_NUMBER': ['min', 'max', 'size','mean'],
                                    'DAYS_INSTALMENT': ['min', 'max', 'size','mean'], 
                                    'AMT_INSTALMENT': ['min', 'max', 'size','mean'], 
                                    'SK_ID_PREV': ['size'], 
                                    }
installments_payments_agg = installments_payments.groupby('SK_ID_CURR').agg(installments_payments_aggregations) 
installments_payments_agg

NUM_INSTALMENT_VERSION                     NUM_INSTALMENT_NUMBER  \
                              min  max size      mean                   min   
SK_ID_CURR                                                                    
100001                        1.0  2.0    7  1.142857                     1   
100002                        1.0  2.0   19  1.052632                     1   
100003                        1.0  2.0   25  1.040000                     1   
100004                        1.0  2.0    3  1.333333                     1   
100005                        1.0  2.0    9  1.111111                     1   
...                           ...  ...  ...       ...                   ...   
456251                        1.0  2.0    7  1.142857                     1   
456252                        1.0  1.0    6  1.000000                     1   
456253                        1.0  1.0   14  1.000000                     1   
456254                        1.0  1.0   19  1.000000                     1   
456255                        1.0  4.0   74  1.824324                     1   

                               DAYS_INSTALMENT                            \
           max size       mean             min     max size         mean   
SK_ID_CURR                                                                 
100001       4    7   2.714286         -2916.0 -1619.0    7 -2187.714286   
100002      19   19  10.000000          -565.0   -25.0   19  -295.000000   
100003      12   25   5.080000         -2310.0  -536.0   25 -1378.160000   
100004       3    3   2.000000          -784.0  -724.0    3  -754.000000   
100005       9    9   5.000000          -706.0  -466.0    9  -586.000000   
...         ..  ...        ...             ...     ...  ...          ...   
456251       7    7   4.000000          -210.0   -30.0    7  -120.000000   
456252       6    6   3.500000         -2466.0 -2316.0    6 -2391.000000   
456253      12   14   4.785714         -2915.0 -1716.0   14 -2372.928571   
456254      10   19   5.263158          -291.0    -7.0   19  -142.263158   
456255      24   74   8.851351          -960.0   -66.0   74  -463.945946   

           AMT_INSTALMENT                                SK_ID_PREV  
                      min         max size          mean       size  
SK_ID_CURR                                                           
100001           3951.000   17397.900    7   5885.132143          7  
100002           9251.775   53093.745   19  11559.247105         19  
100003           6662.970  560835.360   25  64754.586000         25  
100004           5357.250   10573.965    3   7096.155000          3  
100005           4813.200   17656.245    9   6240.205000          9  
...                   ...         ...  ...           ...        ...  
456251           6605.910   12815.010    7   7492.924286          7  
456252          10046.880   10074.465    6  10069.867500          6  
456253           2754.450    5575.185   14   4399.707857         14  
456254           2296.440   19065.825   19  10239.832895         19  
456255          11090.835  615229.515   74  41464.713649         74  

[339587 rows x 17 columns]

In [103]:
installments_payments_agg.columns = pd.Index(['installments_payments_'+e[0] + "_" + e[1].upper() for e in installments_payments_agg.columns.tolist()]) 
installments_payments_agg

installments_payments_NUM_INSTALMENT_VERSION_MIN  \
SK_ID_CURR                                                     
100001                                                   1.0   
100002                                                   1.0   
100003                                                   1.0   
100004                                                   1.0   
100005                                                   1.0   
...                                                      ...   
456251                                                   1.0   
456252                                                   1.0   
456253                                                   1.0   
456254                                                   1.0   
456255                                                   1.0   

            installments_payments_NUM_INSTALMENT_VERSION_MAX  \
SK_ID_CURR                                                     
100001                                                   2.0   
100002                                                   2.0   
100003                                                   2.0   
100004                                                   2.0   
100005                                                   2.0   
...                                                      ...   
456251                                                   2.0   
456252                                                   1.0   
456253                                                   1.0   
456254                                                   1.0   
456255                                                   4.0   

            installments_payments_NUM_INSTALMENT_VERSION_SIZE  \
SK_ID_CURR                                                      
100001                                                      7   
100002                                                     19   
100003                                                     25   
100004                                                      3   
100005                                                      9   
...                                                       ...   
456251                                                      7   
456252                                                      6   
456253                                                     14   
456254                                                     19   
456255                                                     74   

            installments_payments_NUM_INSTALMENT_VERSION_MEAN  \
SK_ID_CURR                                                      
100001                                               1.142857   
100002                                               1.052632   
100003                                               1.040000   
100004                                               1.333333   
100005                                               1.111111   
...                                                       ...   
456251                                               1.142857   
456252                                               1.000000   
456253                                               1.000000   
456254                                               1.000000   
456255                                               1.824324   

            installments_payments_NUM_INSTALMENT_NUMBER_MIN  \
SK_ID_CURR                                                    
100001                                                    1   
100002                                                    1   
100003                                                    1   
100004                                                    1   
100005                                                    1   
...                                                     ...   
456251                                                    1   
456252                                                    1   
456253                  

In [104]:

sk_id_prev_feature = [feature for feature in installments_payments_agg.columns if 'SK_ID_PREV' in feature] 
sk_id_prev_feature

['installments_payments_SK_ID_PREV_SIZE']

In [105]:
installments_payments_agg.rename(columns = {'installments_payments_SK_ID_PREV_SIZE':'installments_payments_PREV_SIZE'}, inplace = True)


In [106]:
_, idx = np.unique(installments_payments_agg, axis = 1, return_index = True)
installments_payments_agg = installments_payments_agg.iloc[:, idx]
installments_payments_agg

installments_payments_DAYS_INSTALMENT_MIN  \
SK_ID_CURR                                              
100001                                        -2916.0   
100002                                         -565.0   
100003                                        -2310.0   
100004                                         -784.0   
100005                                         -706.0   
...                                               ...   
456251                                         -210.0   
456252                                        -2466.0   
456253                                        -2915.0   
456254                                         -291.0   
456255                                         -960.0   

            installments_payments_DAYS_INSTALMENT_MEAN  \
SK_ID_CURR                                               
100001                                    -2187.714286   
100002                                     -295.000000   
100003                                    -1378.160000   
100004                                     -754.000000   
100005                                     -586.000000   
...                                                ...   
456251                                     -120.000000   
456252                                    -2391.000000   
456253                                    -2372.928571   
456254                                     -142.263158   
456255                                     -463.945946   

            installments_payments_DAYS_INSTALMENT_MAX  \
SK_ID_CURR                                              
100001                                        -1619.0   
100002                                          -25.0   
100003                                         -536.0   
100004                                         -724.0   
100005                                         -466.0   
...                                               ...   
456251                                          -30.0   
456252                                        -2316.0   
456253                                        -1716.0   
456254                                           -7.0   
456255                                          -66.0   

            installments_payments_NUM_INSTALMENT_VERSION_MIN  \
SK_ID_CURR                                                     
100001                                                   1.0   
100002                                                   1.0   
100003                                                   1.0   
100004                                                   1.0   
100005                                                   1.0   
...                                                      ...   
456251                                                   1.0   
456252                                                   1.0   
456253                                                   1.0   
456254                                                   1.0   
456255                                                   1.0   

            installments_payments_NUM_INSTALMENT_NUMBER_MIN  \
SK_ID_CURR                                                    
100001                                                    1   
100002                                                    1   
100003                                                    1   
100004                                                    1   
100005                                                    1   
...                                                     ...   
456251                                                    1   
456252                                                    1   
456253                                                    1   
456254                                                    1   
456255                                                    1   

            installments_payments_NUM_INSTALMENT_VERSION_MEAN  \
SK_ID_CURR                                             

In [107]:
installments_payments_agg.std()

installments_payments_DAYS_INSTALMENT_MIN               915.029091
installments_payments_DAYS_INSTALMENT_MEAN              598.571280
installments_payments_DAYS_INSTALMENT_MAX               539.978179
installments_payments_NUM_INSTALMENT_VERSION_MIN          0.419889
installments_payments_NUM_INSTALMENT_NUMBER_MIN           0.747974
installments_payments_NUM_INSTALMENT_VERSION_MEAN         0.620715
installments_payments_NUM_INSTALMENT_VERSION_MAX          1.888141
installments_payments_NUM_INSTALMENT_NUMBER_MEAN         11.405171
installments_payments_NUM_INSTALMENT_NUMBER_MAX          30.162714
installments_payments_NUM_INSTALMENT_VERSION_SIZE        41.053343
installments_payments_AMT_INSTALMENT_MIN              14453.731995
installments_payments_AMT_INSTALMENT_MEAN             23310.595837
installments_payments_AMT_INSTALMENT_MAX             246623.303756
dtype: float64

In [108]:
installments_payments_agg.isnull().sum().sum()

0

In [109]:
gc.enable()
del installments_payments,corr_matrix,upper,to_drop,installments_payments_aggregations,sk_id_prev_feature
gc.collect()

0

## 6. Previous application csv

In [111]:
previous_application = pd.read_csv('previous_application.csv')
previous_application

SK_ID_PREV  SK_ID_CURR NAME_CONTRACT_TYPE  AMT_ANNUITY  \
0           2030495      271877     Consumer loans     1730.430   
1           2802425      108129         Cash loans    25188.615   
2           2523466      122040         Cash loans    15060.735   
3           2819243      176158         Cash loans    47041.335   
4           1784265      202054         Cash loans    31924.395   
...             ...         ...                ...          ...   
1670209     2300464      352015     Consumer loans    14704.290   
1670210     2357031      334635     Consumer loans     6622.020   
1670211     2659632      249544     Consumer loans    11520.855   
1670212     2785582      400317         Cash loans    18821.520   
1670213     2418762      261212         Cash loans    16431.300   

         AMT_APPLICATION  AMT_CREDIT  AMT_DOWN_PAYMENT  AMT_GOODS_PRICE  \
0                17145.0     17145.0               0.0          17145.0   
1               607500.0    679671.0               NaN         607500.0   
2               112500.0    136444.5               NaN         112500.0   
3               450000.0    470790.0               NaN         450000.0   
4               337500.0    404055.0               NaN         337500.0   
...                  ...         ...               ...              ...   
1670209         267295.5    311400.0               0.0         267295.5   
1670210          87750.0     64291.5           29250.0          87750.0   
1670211         105237.0    102523.5           10525.5         105237.0   
1670212         180000.0    191880.0               NaN         180000.0   
1670213         360000.0    360000.0               NaN         360000.0   

        WEEKDAY_APPR_PROCESS_START  HOUR_APPR_PROCESS_START  \
0                         SATURDAY                       15   
1                         THURSDAY                       11   
2                          TUESDAY                       11   
3                           MONDAY                        7   
4                         THURSDAY                        9   
...                            ...                      ...   
1670209                  WEDNESDAY                       12   
1670210                    TUESDAY                       15   
1670211                     MONDAY                       12   
1670212                  WEDNESDAY                        9   
1670213                     SUNDAY                       10   

        FLAG_LAST_APPL_PER_CONTRACT  NFLAG_LAST_APPL_IN_DAY  \
0                                 Y                       1   
1                                 Y                       1   
2                                 Y                       1   
3                                 Y                       1   
4                                 Y                       1   
...                             ...                     ...   
1670209                           Y                       1   
1670210                           Y                       1   
1670211                           Y                       1   
1670212                           Y                       1   
1670213                           Y                       1   

         RATE_DOWN_PAYMENT  RATE_INTEREST_PRIMARY  RATE_INTEREST_PRIVILEGED  \
0                 0.000000               0.182832                  0.867336   
1                      NaN                    NaN                       NaN   
2                      NaN                    NaN                       NaN   
3                      NaN                    NaN                       NaN   
4                      NaN                    NaN                       NaN   
...                    ...                    ...                       ...   
1670209           0.000000                    NaN                       NaN   
1670210           0.340554                    NaN                       NaN   
1670211           0.101401                    NaN                       NaN   

In [112]:
previous_application['DAYS_FIRST_DRAWING'].replace(365243, np.nan, inplace= True)
previous_application['DAYS_FIRST_DUE'].replace(365243, np.nan, inplace= True)
previous_application['DAYS_LAST_DUE_1ST_VERSION'].replace(365243, np.nan, inplace= True)
previous_application['DAYS_LAST_DUE'].replace(365243, np.nan, inplace= True)
previous_application['DAYS_TERMINATION'].replace(365243, np.nan, inplace= True)

## Missing above threshold

In [114]:
previous_application_missing = (previous_application.isnull().sum() / len(previous_application)).sort_values(ascending = False)
previous_application_missing.head()

RATE_INTEREST_PRIVILEGED    0.996437
RATE_INTEREST_PRIMARY       0.996437
DAYS_FIRST_DRAWING          0.962457
DAYS_TERMINATION            0.538241
AMT_DOWN_PAYMENT            0.536365
dtype: float64

calculated the proportion of missing values (NaN) in each column of the previous_application DataFrame. It then sorts the columns by the percentage of missing data in descending order and displays the top columns with the highest missing values 

In [115]:
previous_application_missing = previous_application_missing.index[previous_application_missing > 0.75] # Threshold=0.75

selecting only those columns in the previous_application DataFrame where the proportion of missing values exceeds 75%. The result is a list of column names (previous_application_missing) that have a high percentage of missing data, potentially for further handling or removal.

In [116]:
previous_application = previous_application.drop(columns = previous_application_missing)

## Correlation

In [118]:
threshold = 0.9

# Absolute value correlation matrix
corr_matrix = previous_application.select_dtypes(include=['float64', 'int64']).corr().abs()
corr_matrix.head()

SK_ID_PREV  SK_ID_CURR  AMT_ANNUITY  AMT_APPLICATION  \
SK_ID_PREV         1.000000    0.000321     0.011459         0.003302   
SK_ID_CURR         0.000321    1.000000     0.000577         0.000280   
AMT_ANNUITY        0.011459    0.000577     1.000000         0.808872   
AMT_APPLICATION    0.003302    0.000280     0.808872         1.000000   
AMT_CREDIT         0.003659    0.000195     0.816429         0.975824   

                 AMT_CREDIT  AMT_DOWN_PAYMENT  AMT_GOODS_PRICE  \
SK_ID_PREV         0.003659          0.001313         0.015293   
SK_ID_CURR         0.000195          0.000063         0.000369   
AMT_ANNUITY        0.816429          0.267694         0.820895   
AMT_APPLICATION    0.975824          0.482776         0.999884   
AMT_CREDIT         1.000000          0.301284         0.993087   

                 HOUR_APPR_PROCESS_START  NFLAG_LAST_APPL_IN_DAY  \
SK_ID_PREV                      0.002652                0.002828   
SK_ID_CURR                      0.002842                0.000098   
AMT_ANNUITY                     0.036201                0.020639   
AMT_APPLICATION                 0.014415                0.004310   
AMT_CREDIT                      0.021039                0.025179   

                 RATE_DOWN_PAYMENT  DAYS_DECISION  SELLERPLACE_AREA  \
SK_ID_PREV                0.004051       0.019100          0.001079   
SK_ID_CURR                0.001158       0.000637          0.001265   
AMT_ANNUITY               0.103878       0.279051          0.015027   
AMT_APPLICATION           0.072479       0.133660          0.007649   
AMT_CREDIT                0.188128       0.133763          0.009567   

                 CNT_PAYMENT  DAYS_FIRST_DUE  DAYS_LAST_DUE_1ST_VERSION  \
SK_ID_PREV          0.015589        0.002570                   0.003470   
SK_ID_CURR          0.000031        0.000010                   0.000163   
AMT_ANNUITY         0.394535        0.271278                   0.352772   
AMT_APPLICATION     0.680630        0.267942                   0.463425   
AMT_CREDIT          0.674278        0.272737                   0.482004   

                 DAYS_LAST_DUE  DAYS_TERMINATION  NFLAG_INSURED_ON_APPROVAL  
SK_ID_PREV            0.002212          0.002109                   0.003986  
SK_ID_CURR            0.000940          0.000852                   0.000876  
AMT_ANNUITY           0.305586          0.300777                   0.283080  
AMT_APPLICATION       0.302057          0.296266                   0.259219  
AMT_CREDIT            0.318221          0.318958                   0.263932

In [119]:
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))
upper.head()

SK_ID_PREV  SK_ID_CURR  AMT_ANNUITY  AMT_APPLICATION  \
SK_ID_PREV              NaN    0.000321     0.011459         0.003302   
SK_ID_CURR              NaN         NaN     0.000577         0.000280   
AMT_ANNUITY             NaN         NaN          NaN         0.808872   
AMT_APPLICATION         NaN         NaN          NaN              NaN   
AMT_CREDIT              NaN         NaN          NaN              NaN   

                 AMT_CREDIT  AMT_DOWN_PAYMENT  AMT_GOODS_PRICE  \
SK_ID_PREV         0.003659          0.001313         0.015293   
SK_ID_CURR         0.000195          0.000063         0.000369   
AMT_ANNUITY        0.816429          0.267694         0.820895   
AMT_APPLICATION    0.975824          0.482776         0.999884   
AMT_CREDIT              NaN          0.301284         0.993087   

                 HOUR_APPR_PROCESS_START  NFLAG_LAST_APPL_IN_DAY  \
SK_ID_PREV                      0.002652                0.002828   
SK_ID_CURR                      0.002842                0.000098   
AMT_ANNUITY                     0.036201                0.020639   
AMT_APPLICATION                 0.014415                0.004310   
AMT_CREDIT                      0.021039                0.025179   

                 RATE_DOWN_PAYMENT  DAYS_DECISION  SELLERPLACE_AREA  \
SK_ID_PREV                0.004051       0.019100          0.001079   
SK_ID_CURR                0.001158       0.000637          0.001265   
AMT_ANNUITY               0.103878       0.279051          0.015027   
AMT_APPLICATION           0.072479       0.133660          0.007649   
AMT_CREDIT                0.188128       0.133763          0.009567   

                 CNT_PAYMENT  DAYS_FIRST_DUE  DAYS_LAST_DUE_1ST_VERSION  \
SK_ID_PREV          0.015589        0.002570                   0.003470   
SK_ID_CURR          0.000031        0.000010                   0.000163   
AMT_ANNUITY         0.394535        0.271278                   0.352772   
AMT_APPLICATION     0.680630        0.267942                   0.463425   
AMT_CREDIT          0.674278        0.272737                   0.482004   

                 DAYS_LAST_DUE  DAYS_TERMINATION  NFLAG_INSURED_ON_APPROVAL  
SK_ID_PREV            0.002212          0.002109                   0.003986  
SK_ID_CURR            0.000940          0.000852                   0.000876  
AMT_ANNUITY           0.305586          0.300777                   0.283080  
AMT_APPLICATION       0.302057          0.296266                   0.259219  
AMT_CREDIT            0.318221          0.318958                   0.263932

In [120]:
to_drop = [column for column in upper.columns if any(upper[column] > threshold)]

print('There are %d columns to remove.' % (len(to_drop)))

There are 6 columns to remove.


In [121]:
to_drop

['AMT_CREDIT',
 'AMT_GOODS_PRICE',
 'DAYS_FIRST_DUE',
 'DAYS_LAST_DUE_1ST_VERSION',
 'DAYS_LAST_DUE',
 'DAYS_TERMINATION']

In [122]:
previous_application = previous_application.drop(columns = to_drop)

In [123]:
previous_application

SK_ID_PREV  SK_ID_CURR NAME_CONTRACT_TYPE  AMT_ANNUITY  \
0           2030495      271877     Consumer loans     1730.430   
1           2802425      108129         Cash loans    25188.615   
2           2523466      122040         Cash loans    15060.735   
3           2819243      176158         Cash loans    47041.335   
4           1784265      202054         Cash loans    31924.395   
...             ...         ...                ...          ...   
1670209     2300464      352015     Consumer loans    14704.290   
1670210     2357031      334635     Consumer loans     6622.020   
1670211     2659632      249544     Consumer loans    11520.855   
1670212     2785582      400317         Cash loans    18821.520   
1670213     2418762      261212         Cash loans    16431.300   

         AMT_APPLICATION  AMT_DOWN_PAYMENT WEEKDAY_APPR_PROCESS_START  \
0                17145.0               0.0                   SATURDAY   
1               607500.0               NaN                   THURSDAY   
2               112500.0               NaN                    TUESDAY   
3               450000.0               NaN                     MONDAY   
4               337500.0               NaN                   THURSDAY   
...                  ...               ...                        ...   
1670209         267295.5               0.0                  WEDNESDAY   
1670210          87750.0           29250.0                    TUESDAY   
1670211         105237.0           10525.5                     MONDAY   
1670212         180000.0               NaN                  WEDNESDAY   
1670213         360000.0               NaN                     SUNDAY   

         HOUR_APPR_PROCESS_START FLAG_LAST_APPL_PER_CONTRACT  \
0                             15                           Y   
1                             11                           Y   
2                             11                           Y   
3                              7                           Y   
4                              9                           Y   
...                          ...                         ...   
1670209                       12                           Y   
1670210                       15                           Y   
1670211                       12                           Y   
1670212                        9                           Y   
1670213                       10                           Y   

         NFLAG_LAST_APPL_IN_DAY  RATE_DOWN_PAYMENT NAME_CASH_LOAN_PURPOSE  \
0                             1           0.000000                    XAP   
1                             1                NaN                    XNA   
2                             1                NaN                    XNA   
3                             1                NaN                    XNA   
4                             1                NaN                Repairs   
...                         ...                ...                    ...   
1670209                       1           0.000000                    XAP   
1670210                       1           0.340554                    XAP   
1670211                       1           0.101401                    XAP   
1670212                       1                NaN                    XNA   
1670213                       1                NaN                    XNA   

        NAME_CONTRACT_STATUS  DAYS_DECISION      NAME_PAYMENT_TYPE  \
0                   Approved            -73  Cash through the bank   
1                   Approved           -164                    XNA   
2                   Approved           -301  Cash through the bank   
3                   Approved           -512  Cash through the bank   
4                    Refused           -781  Cash through the bank   
...                      ...            ...                    ...   
1670209             Approved           -544  Cash through the bank   
1670210             Approved          -1694  Cash through the bank   
167

## Outliers handling

In [125]:
previous_application.loc[(previous_application.CNT_PAYMENT>80),'CNT_PAYMENT']=np.median(previous_application.CNT_PAYMENT)
previous_application.loc[(previous_application.SELLERPLACE_AREA>3500000),'SELLERPLACE_AREA']=np.median(previous_application.SELLERPLACE_AREA)
previous_application.loc[(previous_application.AMT_DOWN_PAYMENT>3000000),'AMT_DOWN_PAYMENT']=np.median(previous_application.AMT_DOWN_PAYMENT)
previous_application.loc[(previous_application.AMT_APPLICATION>5000000),'AMT_APPLICATION']=np.median(previous_application.AMT_APPLICATION)
previous_application.loc[(previous_application.AMT_ANNUITY>3500000),'AMT_ANNUITY']=np.median(previous_application.AMT_ANNUITY)

## Handling missing values

In [127]:
previous_application_features_with_na=[features for features in previous_application.columns if previous_application[features].isnull().sum()>0] 
print('The Features that have missing values are as follows: \n',previous_application_features_with_na)
print('The number of Features with missing values are:',len(previous_application_features_with_na))

The Features that have missing values are as follows: 
 ['AMT_ANNUITY', 'AMT_DOWN_PAYMENT', 'RATE_DOWN_PAYMENT', 'NAME_TYPE_SUITE', 'CNT_PAYMENT', 'PRODUCT_COMBINATION', 'NFLAG_INSURED_ON_APPROVAL']
The number of Features with missing values are: 7


In [128]:
previous_application.CNT_PAYMENT=previous_application.CNT_PAYMENT.fillna(0)
previous_application.NFLAG_INSURED_ON_APPROVAL=previous_application.NFLAG_INSURED_ON_APPROVAL.fillna(0) # Categorical - so mode.
previous_application['NAME_TYPE_SUITE'] = previous_application['NAME_TYPE_SUITE'].fillna(previous_application['NAME_TYPE_SUITE'].mode()[0]) # Categorical - so mode.
previous_application['PRODUCT_COMBINATION'] = previous_application['PRODUCT_COMBINATION'].fillna(previous_application['PRODUCT_COMBINATION'].mode()[0]) # Categorical - so mode.
previous_application['AMT_ANNUITY'] = previous_application['AMT_ANNUITY'].fillna(previous_application['AMT_ANNUITY'].median())
previous_application['AMT_DOWN_PAYMENT'] = previous_application['AMT_DOWN_PAYMENT'].fillna(previous_application['AMT_DOWN_PAYMENT'].median())
previous_application['RATE_DOWN_PAYMENT'] = previous_application['RATE_DOWN_PAYMENT'].fillna(previous_application['RATE_DOWN_PAYMENT'].median())

In [129]:
previous_application.isnull().sum().sum()

0

In [130]:
previous_application.FLAG_LAST_APPL_PER_CONTRACT=previous_application.FLAG_LAST_APPL_PER_CONTRACT.map({'Y':1,'N':0})
previous_application.NAME_CONTRACT_STATUS=previous_application.NAME_CONTRACT_STATUS.map({'Approved':3,'Refused':2,'Canceled':1,'Unused offer':0})
previous_application, previous_application_cat = one_hot_encoder(previous_application) 

In [131]:
previous_application

SK_ID_PREV  SK_ID_CURR  AMT_ANNUITY  AMT_APPLICATION  \
0           2030495      271877     1730.430          17145.0   
1           2802425      108129    25188.615         607500.0   
2           2523466      122040    15060.735         112500.0   
3           2819243      176158    47041.335         450000.0   
4           1784265      202054    31924.395         337500.0   
...             ...         ...          ...              ...   
1670209     2300464      352015    14704.290         267295.5   
1670210     2357031      334635     6622.020          87750.0   
1670211     2659632      249544    11520.855         105237.0   
1670212     2785582      400317    18821.520         180000.0   
1670213     2418762      261212    16431.300         360000.0   

         AMT_DOWN_PAYMENT  HOUR_APPR_PROCESS_START  \
0                     0.0                       15   
1                  1638.0                       11   
2                  1638.0                       11   
3                  1638.0                        7   
4                  1638.0                        9   
...                   ...                      ...   
1670209               0.0                       12   
1670210           29250.0                       15   
1670211           10525.5                       12   
1670212            1638.0                        9   
1670213            1638.0                       10   

         FLAG_LAST_APPL_PER_CONTRACT  NFLAG_LAST_APPL_IN_DAY  \
0                                  1                       1   
1                                  1                       1   
2                                  1                       1   
3                                  1                       1   
4                                  1                       1   
...                              ...                     ...   
1670209                            1                       1   
1670210                            1                       1   
1670211                            1                       1   
1670212                            1                       1   
1670213                            1                       1   

         RATE_DOWN_PAYMENT  NAME_CONTRACT_STATUS  DAYS_DECISION  \
0                 0.000000                     3            -73   
1                 0.051605                     3           -164   
2                 0.051605                     3           -301   
3                 0.051605                     3           -512   
4                 0.051605                     2           -781   
...                    ...                   ...            ...   
1670209           0.000000                     3           -544   
1670210           0.340554                     3          -1694   
1670211           0.101401                     3          -1488   
1670212           0.051605                     3          -1185   
1670213           0.051605                     3          -1193   

         SELLERPLACE_AREA  CNT_PAYMENT  NFLAG_INSURED_ON_APPROVAL  \
0                      35         12.0                        0.0   
1                      -1         36.0                        1.0   
2                      -1         12.0                        1.0   
3                      -1         12.0                        1.0   
4                      -1         24.0                        0.0   
...                   ...          ...                        ...   
1670209                43         30.0                        0.0   
1670210                43         12.0                        0.0   
1670211              1370         10.0                        0.0   
1670212                -1         12.0                        1.0   
1670213                -1         48.0                        0.0   

         NAME_CONTRACT_TYPE_Cash loans  NAME_CONTRACT_TYPE_Consumer loans  \
0                                False                               True   
1                     

In [132]:
previous_application_cat

['NAME_CONTRACT_TYPE_Cash loans',
 'NAME_CONTRACT_TYPE_Consumer loans',
 'NAME_CONTRACT_TYPE_Revolving loans',
 'NAME_CONTRACT_TYPE_XNA',
 'WEEKDAY_APPR_PROCESS_START_FRIDAY',
 'WEEKDAY_APPR_PROCESS_START_MONDAY',
 'WEEKDAY_APPR_PROCESS_START_SATURDAY',
 'WEEKDAY_APPR_PROCESS_START_SUNDAY',
 'WEEKDAY_APPR_PROCESS_START_THURSDAY',
 'WEEKDAY_APPR_PROCESS_START_TUESDAY',
 'WEEKDAY_APPR_PROCESS_START_WEDNESDAY',
 'NAME_CASH_LOAN_PURPOSE_Building a house or an annex',
 'NAME_CASH_LOAN_PURPOSE_Business development',
 'NAME_CASH_LOAN_PURPOSE_Buying a garage',
 'NAME_CASH_LOAN_PURPOSE_Buying a holiday home / land',
 'NAME_CASH_LOAN_PURPOSE_Buying a home',
 'NAME_CASH_LOAN_PURPOSE_Buying a new car',
 'NAME_CASH_LOAN_PURPOSE_Buying a used car',
 'NAME_CASH_LOAN_PURPOSE_Car repairs',
 'NAME_CASH_LOAN_PURPOSE_Education',
 'NAME_CASH_LOAN_PURPOSE_Everyday expenses',
 'NAME_CASH_LOAN_PURPOSE_Furniture',
 'NAME_CASH_LOAN_PURPOSE_Gasification / water supply',
 'NAME_CASH_LOAN_PURPOSE_Hobby',
 'NAME_CA

## Aggregation

In [134]:
previous_application_numerical_col=[feature for feature in previous_application.columns if feature not in previous_application_cat+['SK_ID_CURR','SK_ID_PREV']]
previous_application_aggregations = {'SK_ID_PREV': ['size']}

for col in previous_application_numerical_col:
    previous_application_aggregations[col] = ['min','max','mean','sum']
    
for col in previous_application_cat:
    previous_application_aggregations[col] = ['mean','sum']
    
previous_application_agg = previous_application.groupby('SK_ID_CURR').agg(previous_application_aggregations) 
previous_application_agg

SK_ID_PREV AMT_ANNUITY                                       \
                 size         min        max          mean         sum   
SK_ID_CURR                                                               
100001              1    3951.000   3951.000   3951.000000    3951.000   
100002              1    9251.775   9251.775   9251.775000    9251.775   
100003              3    6737.310  98356.995  56553.990000  169661.970   
100004              1    5357.250   5357.250   5357.250000    5357.250   
100005              2    4813.200  11250.000   8031.600000   16063.200   
...               ...         ...        ...           ...         ...   
456251              1    6605.910   6605.910   6605.910000    6605.910   
456252              1   10074.465  10074.465  10074.465000   10074.465   
456253              2    3973.095   5567.715   4770.405000    9540.810   
456254              2    2296.440  19065.825  10681.132500   21362.265   
456255              8    2250.000  54022.140  20775.391875  166203.135   

           AMT_APPLICATION                                   AMT_DOWN_PAYMENT  \
                       min        max        mean        sum              min   
SK_ID_CURR                                                                      
100001             24835.5    24835.5   24835.500    24835.5           2520.0   
100002            179055.0   179055.0  179055.000   179055.0              0.0   
100003             68809.5   900000.0  435436.500  1306309.5              0.0   
100004             24282.0    24282.0   24282.000    24282.0           4860.0   
100005                 0.0    44617.5   22308.750    44617.5           1638.0   
...                    ...        ...         ...        ...              ...   
456251             40455.0    40455.0   40455.000    40455.0              0.0   
456252             57595.5    57595.5   57595.500    57595.5           3456.0   
456253             19413.0    28912.5   24162.750    48325.5           2893.5   
456254             18846.0   223789.5  121317.750   242635.5              0.0   
456255             45000.0  1170000.0  362770.875  2902167.0              0.0   

                                      HOUR_APPR_PROCESS_START                 \
               max      mean      sum                     min max       mean   
SK_ID_CURR                                                                     
100001      2520.0  2520.000   2520.0                      13  13  13.000000   
100002         0.0     0.000      0.0                       9   9   9.000000   
100003      6885.0  2841.000   8523.0                      12  17  14.666667   
100004      4860.0  4860.000   4860.0                       5   5   5.000000   
100005      4464.0  3051.000   6102.0                      10  11  10.500000   
...            ...       ...      ...                     ...  ..        ...   
456251         0.0     0.000      0.0                      17  17  17.000000   
456252      3456.0  3456.000   3456.0                      10  10  10.000000   
456253      5913.0  4403.250   8806.5                      11  12  11.500000   
456254         0.0     0.000      0.0                      12  18  15.000000   
456255      9000.0  2876.625  23013.0                      12  18  14.625000   

                FLAG_LAST_APPL_PER_CONTRACT               \
            sum                         min max mean sum   
SK_ID_CURR                                                 
100001       13                           1   1  1.0   1   
100002        9                           1   1  1.0   1   
100003       44                           1   1  1.0   3   
100004        5                           1   1  1.0   1   
100005       21                           1   1  1.0   2   
...         ...                         ...  ..  ...  ..   
456251       17                           1   1  1.0   1   
456252       10                           1   1  1.0   1   
456253       23                           1   1  1.0   2  

In [135]:
previous_application_agg.columns = pd.Index(['previous_application_'+e[0] + "_" + e[1].upper() for e in previous_application_agg.columns.tolist()]) 
previous_application_agg

previous_application_SK_ID_PREV_SIZE  \
SK_ID_CURR                                         
100001                                         1   
100002                                         1   
100003                                         3   
100004                                         1   
100005                                         2   
...                                          ...   
456251                                         1   
456252                                         1   
456253                                         2   
456254                                         2   
456255                                         8   

            previous_application_AMT_ANNUITY_MIN  \
SK_ID_CURR                                         
100001                                  3951.000   
100002                                  9251.775   
100003                                  6737.310   
100004                                  5357.250   
100005                                  4813.200   
...                                          ...   
456251                                  6605.910   
456252                                 10074.465   
456253                                  3973.095   
456254                                  2296.440   
456255                                  2250.000   

            previous_application_AMT_ANNUITY_MAX  \
SK_ID_CURR                                         
100001                                  3951.000   
100002                                  9251.775   
100003                                 98356.995   
100004                                  5357.250   
100005                                 11250.000   
...                                          ...   
456251                                  6605.910   
456252                                 10074.465   
456253                                  5567.715   
456254                                 19065.825   
456255                                 54022.140   

            previous_application_AMT_ANNUITY_MEAN  \
SK_ID_CURR                                          
100001                                3951.000000   
100002                                9251.775000   
100003                               56553.990000   
100004                                5357.250000   
100005                                8031.600000   
...                                           ...   
456251                                6605.910000   
456252                               10074.465000   
456253                                4770.405000   
456254                               10681.132500   
456255                               20775.391875   

            previous_application_AMT_ANNUITY_SUM  \
SK_ID_CURR                                         
100001                                  3951.000   
100002                                  9251.775   
100003                                169661.970   
100004                                  5357.250   
100005                                 16063.200   
...                                          ...   
456251                                  6605.910   
456252                                 10074.465   
456253                                  9540.810   
456254                                 21362.265   
456255                                166203.135   

            previous_application_AMT_APPLICATION_MIN  \
SK_ID_CURR                                             
100001                                       24835.5   
100002                                      179055.0   
100003                                       68809.5   
100004                                       24282.0   
100005                                           0.0   
...                                              ...   
456251                                       40455.0   
456252                                       57595.5   
456253                                       19413.0  

In [136]:
sk_id_prev_feature = [feature for feature in previous_application_agg.columns if 'SK_ID_PREV' in feature] 
sk_id_prev_feature

['previous_application_SK_ID_PREV_SIZE']

In [137]:
previous_application_agg.rename(columns = {'previous_application_SK_ID_PREV_SIZE':'previous_application_PREV_SIZE'}, inplace = True)

In [138]:
_, idx = np.unique(previous_application_agg, axis = 1, return_index = True)
previous_application_agg = previous_application_agg.iloc[:, idx]
previous_application_agg

previous_application_DAYS_DECISION_SUM  \
SK_ID_CURR                                           
100001                                       -1740   
100002                                        -606   
100003                                       -3915   
100004                                        -815   
100005                                       -1072   
...                                            ...   
456251                                        -273   
456252                                       -2497   
456253                                       -4760   
456254                                        -599   
456255                                       -4701   

            previous_application_DAYS_DECISION_MIN  \
SK_ID_CURR                                           
100001                                       -1740   
100002                                        -606   
100003                                       -2341   
100004                                        -815   
100005                                        -757   
...                                            ...   
456251                                        -273   
456252                                       -2497   
456253                                       -2851   
456254                                        -322   
456255                                        -991   

            previous_application_DAYS_DECISION_MEAN  \
SK_ID_CURR                                            
100001                                    -1740.000   
100002                                     -606.000   
100003                                    -1305.000   
100004                                     -815.000   
100005                                     -536.000   
...                                             ...   
456251                                     -273.000   
456252                                    -2497.000   
456253                                    -2380.000   
456254                                     -299.500   
456255                                     -587.625   

            previous_application_DAYS_DECISION_MAX  \
SK_ID_CURR                                           
100001                                       -1740   
100002                                        -606   
100003                                        -746   
100004                                        -815   
100005                                        -315   
...                                            ...   
456251                                        -273   
456252                                       -2497   
456253                                       -1909   
456254                                        -277   
456255                                        -171   

            previous_application_NAME_GOODS_CATEGORY_Animals_MEAN  \
SK_ID_CURR                                                          
100001                                                    0.0       
100002                                                    0.0       
100003                                                    0.0       
100004                                                    0.0       
100005                                                    0.0       
...                                                       ...       
456251                                                    0.0       
456252                                                    0.0       
456253                                                    0.0       
456254                                                    0.0       
456255                                                    0.0       

            previous_application_NAME_GOODS_CATEGORY_Animals_SUM  \
SK_ID_CURR                                                         
100001                                                      0      
100002                                                      0      
100003           

In [139]:
pd.set_option('display.max_rows',None) 

In [140]:
previous_application_agg.std()

previous_application_DAYS_DECISION_SUM                                                   4.306790e+03
previous_application_DAYS_DECISION_MIN                                                   8.653665e+02
previous_application_DAYS_DECISION_MEAN                                                  5.746590e+02
previous_application_DAYS_DECISION_MAX                                                   5.369257e+02
previous_application_NAME_GOODS_CATEGORY_Animals_MEAN                                    5.726253e-04
previous_application_NAME_GOODS_CATEGORY_Animals_SUM                                     1.717876e-03
previous_application_NAME_GOODS_CATEGORY_House Construction_MEAN                         2.454108e-04
previous_application_NAME_GOODS_CATEGORY_House Construction_SUM                          1.717876e-03
previous_application_NAME_CASH_LOAN_PURPOSE_Refusal to name the goal_MEAN                1.996739e-03
previous_application_NAME_CASH_LOAN_PURPOSE_Refusal to name the goal_SUM          

In [141]:
pd.reset_option('display.max_rows') 

In [142]:
previous_application_agg=previous_application_agg.drop(columns='previous_application_FLAG_LAST_APPL_PER_CONTRACT_MAX')
previous_application_agg.info()

<class 'pandas.core.frame.DataFrame'>
Index: 338857 entries, 100001 to 456255
Columns: 322 entries, previous_application_DAYS_DECISION_SUM to previous_application_AMT_APPLICATION_SUM
dtypes: float64(167), int64(155)
memory usage: 835.0 MB


In [143]:
previous_application_agg.isnull().sum().sum()

0

In [144]:
gc.enable()
del previous_application,previous_application_missing,corr_matrix,upper,to_drop,previous_application_cat,previous_application_numerical_col,previous_application_aggregations,sk_id_prev_feature
gc.collect()

0

## 8. Application_train Data

In [146]:
app_train=pd.read_csv("application_train.csv")
app_train

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0           100002       1         Cash loans           M            N   
1           100003       0         Cash loans           F            N   
2           100004       0    Revolving loans           M            Y   
3           100006       0         Cash loans           F            N   
4           100007       0         Cash loans           M            N   
...            ...     ...                ...         ...          ...   
307506      456251       0         Cash loans           M            N   
307507      456252       0         Cash loans           F            N   
307508      456253       0         Cash loans           F            N   
307509      456254       1         Cash loans           F            N   
307510      456255       0         Cash loans           F            N   

       FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
0                    Y             0          202500.0    406597.5   
1                    N             0          270000.0   1293502.5   
2                    Y             0           67500.0    135000.0   
3                    Y             0          135000.0    312682.5   
4                    Y             0          121500.0    513000.0   
...                ...           ...               ...         ...   
307506               N             0          157500.0    254700.0   
307507               Y             0           72000.0    269550.0   
307508               Y             0          153000.0    677664.0   
307509               Y             0          171000.0    370107.0   
307510               N             0          157500.0    675000.0   

        AMT_ANNUITY  AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
0           24700.5         351000.0   Unaccompanied               Working   
1           35698.5        1129500.0          Family         State servant   
2            6750.0         135000.0   Unaccompanied               Working   
3           29686.5         297000.0   Unaccompanied               Working   
4           21865.5         513000.0   Unaccompanied               Working   
...             ...              ...             ...                   ...   
307506      27558.0         225000.0   Unaccompanied               Working   
307507      12001.5         225000.0   Unaccompanied             Pensioner   
307508      29979.0         585000.0   Unaccompanied               Working   
307509      20205.0         319500.0   Unaccompanied  Commercial associate   
307510      49117.5         675000.0   Unaccompanied  Commercial associate   

                  NAME_EDUCATION_TYPE    NAME_FAMILY_STATUS  \
0       Secondary / secondary special  Single / not married   
1                    Higher education               Married   
2       Secondary / secondary special  Single / not married   
3       Secondary / secondary special        Civil marriage   
4       Secondary / secondary special  Single / not married   
...                               ...                   ...   
307506  Secondary / secondary special             Separated   
307507  Secondary / secondary special                 Widow   
307508               Higher education             Separated   
307509  Secondary / secondary special               Married   
307510               Higher education               Married   

        NAME_HOUSING_TYPE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
0       House / apartment                    0.018801       -9461   
1       House / apartment                    0.003541      -16765   
2       House / apartment                    0.010032      -19046   
3       House / apartment                    0.008019      -19005   
4       House / apartment                    0.028663      -19932   
...                   ...                         ...         ...   
307506       With parents                    0.032561       -9327   
307507  House / apartment       

In [147]:
app_train = app_train[app_train['CODE_GENDER'] != 'XNA']
app_train.info()

<class 'pandas.core.frame.DataFrame'>
Index: 307507 entries, 0 to 307510
Columns: 122 entries, SK_ID_CURR to AMT_REQ_CREDIT_BUREAU_YEAR
dtypes: float64(65), int64(41), object(16)
memory usage: 288.6+ MB


 filters out rows in the app_train DataFrame where the CODE_GENDER column has the value 'XNA', which likely represents invalid or missing gender data.

In [148]:
app_train['DAYS_EMPLOYED'].replace(365243, np.nan, inplace= True)

replacing the value 365243 in the DAYS_EMPLOYED column of the app_train DataFrame with NaN. The value 365243 is often used to indicate missing or unknown employment duration, so it is replaced to ensure accurate data processing and analysis.

In [149]:
threshold = 0.9

# Absolute value correlation matrix
corr_matrix = app_train.select_dtypes(include=['float64', 'int64']).corr().abs()
corr_matrix.head()

SK_ID_CURR    TARGET  CNT_CHILDREN  AMT_INCOME_TOTAL  \
SK_ID_CURR          1.000000  0.002111      0.001120          0.001821   
TARGET              0.002111  1.000000      0.019189          0.003982   
CNT_CHILDREN        0.001120  0.019189      1.000000          0.012884   
AMT_INCOME_TOTAL    0.001821  0.003982      0.012884          1.000000   
AMT_CREDIT          0.000350  0.030371      0.002151          0.156871   

                  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
SK_ID_CURR          0.000350     0.000440         0.000241   
TARGET              0.030371     0.012818         0.039647   
CNT_CHILDREN        0.002151     0.021381         0.001818   
AMT_INCOME_TOTAL    0.156871     0.191658         0.159610   
AMT_CREDIT          1.000000     0.770137         0.986971   

                  REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
SK_ID_CURR                          0.000852    0.001500       0.000101   
TARGET                              0.037225    0.078242       0.074957   
CNT_CHILDREN                        0.025577    0.330937       0.061139   
AMT_INCOME_TOTAL                    0.074795    0.027261       0.013003   
AMT_CREDIT                          0.099742    0.055434       0.091304   

                  DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
SK_ID_CURR                 0.000973         0.000389     0.001821    0.002804   
TARGET                     0.041976         0.051457     0.037611    0.000534   
CNT_CHILDREN               0.183387         0.028014     0.008492    0.001041   
AMT_INCOME_TOTAL           0.027807         0.008506     0.117272    0.000325   
AMT_CREDIT                 0.009623         0.006577     0.094191    0.001436   

                  FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  \
SK_ID_CURR              0.001332         0.000395          0.002815   
TARGET                  0.045984         0.028533          0.000370   
CNT_CHILDREN            0.240713         0.055620          0.000794   
AMT_INCOME_TOTAL        0.063994         0.017195          0.008290   
AMT_CREDIT              0.065522         0.021072          0.023653   

                  FLAG_PHONE  FLAG_EMAIL  CNT_FAM_MEMBERS  \
SK_ID_CURR          0.002769    0.000278         0.002885   
TARGET              0.023801    0.001759         0.009310   
CNT_CHILDREN        0.029916    0.022620         0.879159   
AMT_INCOME_TOTAL    0.000157    0.038378         0.016343   
AMT_CREDIT          0.026224    0.016630         0.063167   

                  REGION_RATING_CLIENT  REGION_RATING_CLIENT_W_CITY  \
SK_ID_CURR                    0.001067                     0.001130   
TARGET                        0.058901                     0.060895   
CNT_CHILDREN                  0.025428                     0.024786   
AMT_INCOME_TOTAL              0.085467                     0.091736   
AMT_CREDIT                    0.101774                     0.110913   

                  HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
SK_ID_CURR                       0.000354                    0.000284   
TARGET                           0.024164                    0.005575   
CNT_CHILDREN                     0.007303                    0.013319   
AMT_INCOME_TOTAL                 0.036459                    0.031191   
AMT_CREDIT                       0.052742                    0.024009   

                  REG_REGION_NOT_WORK_REGION  LIVE_REGION_NOT_WORK_REGION  \
SK_ID_CURR                          0.001095                     0.002901   
TARGET                              0.006941                     0.002819   
CNT_CHILDREN                        0.008186                     0.014836   
AMT_INCOME_TOTAL                    0.062341                     0.058059   
AMT_CREDIT                          0.051928                     0.052608   

                  REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  \
SK_ID_CURR                      0.001888                0.001588   
TAR

In [150]:
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))
upper.head()

SK_ID_CURR    TARGET  CNT_CHILDREN  AMT_INCOME_TOTAL  \
SK_ID_CURR               NaN  0.002111      0.001120          0.001821   
TARGET                   NaN       NaN      0.019189          0.003982   
CNT_CHILDREN             NaN       NaN           NaN          0.012884   
AMT_INCOME_TOTAL         NaN       NaN           NaN               NaN   
AMT_CREDIT               NaN       NaN           NaN               NaN   

                  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
SK_ID_CURR          0.000350     0.000440         0.000241   
TARGET              0.030371     0.012818         0.039647   
CNT_CHILDREN        0.002151     0.021381         0.001818   
AMT_INCOME_TOTAL    0.156871     0.191658         0.159610   
AMT_CREDIT               NaN     0.770137         0.986971   

                  REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
SK_ID_CURR                          0.000852    0.001500       0.000101   
TARGET                              0.037225    0.078242       0.074957   
CNT_CHILDREN                        0.025577    0.330937       0.061139   
AMT_INCOME_TOTAL                    0.074795    0.027261       0.013003   
AMT_CREDIT                          0.099742    0.055434       0.091304   

                  DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
SK_ID_CURR                 0.000973         0.000389     0.001821    0.002804   
TARGET                     0.041976         0.051457     0.037611    0.000534   
CNT_CHILDREN               0.183387         0.028014     0.008492    0.001041   
AMT_INCOME_TOTAL           0.027807         0.008506     0.117272    0.000325   
AMT_CREDIT                 0.009623         0.006577     0.094191    0.001436   

                  FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  \
SK_ID_CURR              0.001332         0.000395          0.002815   
TARGET                  0.045984         0.028533          0.000370   
CNT_CHILDREN            0.240713         0.055620          0.000794   
AMT_INCOME_TOTAL        0.063994         0.017195          0.008290   
AMT_CREDIT              0.065522         0.021072          0.023653   

                  FLAG_PHONE  FLAG_EMAIL  CNT_FAM_MEMBERS  \
SK_ID_CURR          0.002769    0.000278         0.002885   
TARGET              0.023801    0.001759         0.009310   
CNT_CHILDREN        0.029916    0.022620         0.879159   
AMT_INCOME_TOTAL    0.000157    0.038378         0.016343   
AMT_CREDIT          0.026224    0.016630         0.063167   

                  REGION_RATING_CLIENT  REGION_RATING_CLIENT_W_CITY  \
SK_ID_CURR                    0.001067                     0.001130   
TARGET                        0.058901                     0.060895   
CNT_CHILDREN                  0.025428                     0.024786   
AMT_INCOME_TOTAL              0.085467                     0.091736   
AMT_CREDIT                    0.101774                     0.110913   

                  HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
SK_ID_CURR                       0.000354                    0.000284   
TARGET                           0.024164                    0.005575   
CNT_CHILDREN                     0.007303                    0.013319   
AMT_INCOME_TOTAL                 0.036459                    0.031191   
AMT_CREDIT                       0.052742                    0.024009   

                  REG_REGION_NOT_WORK_REGION  LIVE_REGION_NOT_WORK_REGION  \
SK_ID_CURR                          0.001095                     0.002901   
TARGET                              0.006941                     0.002819   
CNT_CHILDREN                        0.008186                     0.014836   
AMT_INCOME_TOTAL                    0.062341                     0.058059   
AMT_CREDIT                          0.051928                     0.052608   

                  REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  \
SK_ID_CURR                      0.001888                0.001588   
TAR

In [151]:
to_drop = [column for column in upper.columns if any(upper[column] > threshold)]

print('There are %d columns to remove.' % (len(to_drop)))

There are 34 columns to remove.


In [152]:
to_drop

['AMT_GOODS_PRICE',
 'REGION_RATING_CLIENT_W_CITY',
 'LIVINGAPARTMENTS_AVG',
 'LIVINGAREA_AVG',
 'APARTMENTS_MODE',
 'BASEMENTAREA_MODE',
 'YEARS_BEGINEXPLUATATION_MODE',
 'YEARS_BUILD_MODE',
 'COMMONAREA_MODE',
 'ELEVATORS_MODE',
 'ENTRANCES_MODE',
 'FLOORSMAX_MODE',
 'FLOORSMIN_MODE',
 'LANDAREA_MODE',
 'LIVINGAPARTMENTS_MODE',
 'LIVINGAREA_MODE',
 'NONLIVINGAPARTMENTS_MODE',
 'NONLIVINGAREA_MODE',
 'APARTMENTS_MEDI',
 'BASEMENTAREA_MEDI',
 'YEARS_BEGINEXPLUATATION_MEDI',
 'YEARS_BUILD_MEDI',
 'COMMONAREA_MEDI',
 'ELEVATORS_MEDI',
 'ENTRANCES_MEDI',
 'FLOORSMAX_MEDI',
 'FLOORSMIN_MEDI',
 'LANDAREA_MEDI',
 'LIVINGAPARTMENTS_MEDI',
 'LIVINGAREA_MEDI',
 'NONLIVINGAPARTMENTS_MEDI',
 'NONLIVINGAREA_MEDI',
 'TOTALAREA_MODE',
 'OBS_60_CNT_SOCIAL_CIRCLE']

In [153]:
app_train = app_train.drop(columns = to_drop)

Dropping the columns above threshold value

In [154]:
app_train

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0           100002       1         Cash loans           M            N   
1           100003       0         Cash loans           F            N   
2           100004       0    Revolving loans           M            Y   
3           100006       0         Cash loans           F            N   
4           100007       0         Cash loans           M            N   
...            ...     ...                ...         ...          ...   
307506      456251       0         Cash loans           M            N   
307507      456252       0         Cash loans           F            N   
307508      456253       0         Cash loans           F            N   
307509      456254       1         Cash loans           F            N   
307510      456255       0         Cash loans           F            N   

       FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
0                    Y             0          202500.0    406597.5   
1                    N             0          270000.0   1293502.5   
2                    Y             0           67500.0    135000.0   
3                    Y             0          135000.0    312682.5   
4                    Y             0          121500.0    513000.0   
...                ...           ...               ...         ...   
307506               N             0          157500.0    254700.0   
307507               Y             0           72000.0    269550.0   
307508               Y             0          153000.0    677664.0   
307509               Y             0          171000.0    370107.0   
307510               N             0          157500.0    675000.0   

        AMT_ANNUITY NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
0           24700.5   Unaccompanied               Working   
1           35698.5          Family         State servant   
2            6750.0   Unaccompanied               Working   
3           29686.5   Unaccompanied               Working   
4           21865.5   Unaccompanied               Working   
...             ...             ...                   ...   
307506      27558.0   Unaccompanied               Working   
307507      12001.5   Unaccompanied             Pensioner   
307508      29979.0   Unaccompanied               Working   
307509      20205.0   Unaccompanied  Commercial associate   
307510      49117.5   Unaccompanied  Commercial associate   

                  NAME_EDUCATION_TYPE    NAME_FAMILY_STATUS  \
0       Secondary / secondary special  Single / not married   
1                    Higher education               Married   
2       Secondary / secondary special  Single / not married   
3       Secondary / secondary special        Civil marriage   
4       Secondary / secondary special  Single / not married   
...                               ...                   ...   
307506  Secondary / secondary special             Separated   
307507  Secondary / secondary special                 Widow   
307508               Higher education             Separated   
307509  Secondary / secondary special               Married   
307510               Higher education               Married   

        NAME_HOUSING_TYPE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
0       House / apartment                    0.018801       -9461   
1       House / apartment                    0.003541      -16765   
2       House / apartment                    0.010032      -19046   
3       House / apartment                    0.008019      -19005   
4       House / apartment                    0.028663      -19932   
...                   ...                         ...         ...   
307506       With parents                    0.032561       -9327   
307507  House / apartment                    0.025164      -20775   
307508  House / apartment                    0.005002      -14966   
307509  House / apartment                    0.005313      -11961   
307510  House / apartment    

In [155]:
app_train.loc[(app_train.OBS_30_CNT_SOCIAL_CIRCLE>45),'OBS_30_CNT_SOCIAL_CIRCLE']=np.median(app_train.OBS_30_CNT_SOCIAL_CIRCLE)
app_train.loc[(app_train.DEF_30_CNT_SOCIAL_CIRCLE>20),'DEF_30_CNT_SOCIAL_CIRCLE']=np.median(app_train.DEF_30_CNT_SOCIAL_CIRCLE)
app_train.loc[(app_train.DEF_60_CNT_SOCIAL_CIRCLE>20),'DEF_60_CNT_SOCIAL_CIRCLE']=np.median(app_train.DEF_60_CNT_SOCIAL_CIRCLE)
app_train.loc[(app_train.CNT_FAM_MEMBERS>15.0),'CNT_FAM_MEMBERS']=np.median(app_train.CNT_FAM_MEMBERS)
app_train.loc[(app_train.CNT_CHILDREN>12.0),'CNT_CHILDREN']=np.median(app_train.CNT_CHILDREN)
app_train.loc[(app_train.OWN_CAR_AGE>60),'OWN_CAR_AGE']=np.median(app_train.OWN_CAR_AGE)
app_train.loc[(app_train.REGION_POPULATION_RELATIVE>0.07),'REGION_POPULATION_RELATIVE']=np.median(app_train.REGION_POPULATION_RELATIVE)
app_train.loc[(app_train.AMT_ANNUITY>250000),'AMT_ANNUITY']=np.median(app_train.AMT_ANNUITY)
app_train.loc[(app_train.AMT_CREDIT>4000000),'AMT_CREDIT']=np.median(app_train.AMT_CREDIT) 
app_train.loc[(app_train.AMT_INCOME_TOTAL>100000000),'AMT_INCOME_TOTAL']=np.median(app_train.AMT_INCOME_TOTAL) 
app_train.loc[(app_train.YEARS_BEGINEXPLUATATION_AVG<0.2),'YEARS_BEGINEXPLUATATION_AVG']=np.median(app_train.YEARS_BEGINEXPLUATATION_AVG) 

In [156]:
app_train_features_with_na=[features for features in app_train.columns if app_train[features].isnull().sum()>0] 
print('The Features that have missing values are as follows: \n',app_train_features_with_na)
print('The number of Features with missing values are:',len(app_train_features_with_na))

The Features that have missing values are as follows: 
 ['AMT_ANNUITY', 'NAME_TYPE_SUITE', 'DAYS_EMPLOYED', 'OWN_CAR_AGE', 'OCCUPATION_TYPE', 'CNT_FAM_MEMBERS', 'EXT_SOURCE_1', 'EXT_SOURCE_2', 'EXT_SOURCE_3', 'APARTMENTS_AVG', 'BASEMENTAREA_AVG', 'YEARS_BEGINEXPLUATATION_AVG', 'YEARS_BUILD_AVG', 'COMMONAREA_AVG', 'ELEVATORS_AVG', 'ENTRANCES_AVG', 'FLOORSMAX_AVG', 'FLOORSMIN_AVG', 'LANDAREA_AVG', 'NONLIVINGAPARTMENTS_AVG', 'NONLIVINGAREA_AVG', 'FONDKAPREMONT_MODE', 'HOUSETYPE_MODE', 'WALLSMATERIAL_MODE', 'EMERGENCYSTATE_MODE', 'OBS_30_CNT_SOCIAL_CIRCLE', 'DEF_30_CNT_SOCIAL_CIRCLE', 'DEF_60_CNT_SOCIAL_CIRCLE', 'DAYS_LAST_PHONE_CHANGE', 'AMT_REQ_CREDIT_BUREAU_HOUR', 'AMT_REQ_CREDIT_BUREAU_DAY', 'AMT_REQ_CREDIT_BUREAU_WEEK', 'AMT_REQ_CREDIT_BUREAU_MON', 'AMT_REQ_CREDIT_BUREAU_QRT', 'AMT_REQ_CREDIT_BUREAU_YEAR']
The number of Features with missing values are: 35


In [157]:
app_train.CNT_FAM_MEMBERS=app_train.CNT_FAM_MEMBERS.fillna(0)
app_train['NAME_TYPE_SUITE'] = app_train['NAME_TYPE_SUITE'].fillna(app_train['NAME_TYPE_SUITE'].mode()[0]) 
app_train['OCCUPATION_TYPE'] = app_train['OCCUPATION_TYPE'].fillna(app_train['OCCUPATION_TYPE'].mode()[0]) 
app_train['FONDKAPREMONT_MODE'] = app_train['FONDKAPREMONT_MODE'].fillna(app_train['FONDKAPREMONT_MODE'].mode()[0])
app_train['HOUSETYPE_MODE'] = app_train['HOUSETYPE_MODE'].fillna(app_train['HOUSETYPE_MODE'].mode()[0])
app_train['WALLSMATERIAL_MODE'] = app_train['WALLSMATERIAL_MODE'].fillna(app_train['WALLSMATERIAL_MODE'].mode()[0])
app_train['EMERGENCYSTATE_MODE'] = app_train['EMERGENCYSTATE_MODE'].fillna(app_train['EMERGENCYSTATE_MODE'].mode()[0])
app_train['AMT_ANNUITY'] = app_train['AMT_ANNUITY'].fillna(app_train['AMT_ANNUITY'].median())
app_train['AMT_REQ_CREDIT_BUREAU_HOUR'] = app_train['AMT_REQ_CREDIT_BUREAU_HOUR'].fillna(app_train['AMT_REQ_CREDIT_BUREAU_HOUR'].median())
app_train['AMT_REQ_CREDIT_BUREAU_DAY'] = app_train['AMT_REQ_CREDIT_BUREAU_DAY'].fillna(app_train['AMT_REQ_CREDIT_BUREAU_DAY'].median())
app_train['AMT_REQ_CREDIT_BUREAU_WEEK'] = app_train['AMT_REQ_CREDIT_BUREAU_WEEK'].fillna(app_train['AMT_REQ_CREDIT_BUREAU_WEEK'].median())
app_train['AMT_REQ_CREDIT_BUREAU_MON'] = app_train['AMT_REQ_CREDIT_BUREAU_MON'].fillna(app_train['AMT_REQ_CREDIT_BUREAU_MON'].median())
app_train['AMT_REQ_CREDIT_BUREAU_QRT'] = app_train['AMT_REQ_CREDIT_BUREAU_QRT'].fillna(app_train['AMT_REQ_CREDIT_BUREAU_QRT'].median())
app_train['AMT_REQ_CREDIT_BUREAU_YEAR'] = app_train['AMT_REQ_CREDIT_BUREAU_YEAR'].fillna(app_train['AMT_REQ_CREDIT_BUREAU_YEAR'].median())

In [158]:
app_train['DAYS_EMPLOYED'] = app_train['DAYS_EMPLOYED'].fillna(app_train['DAYS_EMPLOYED'].median())
app_train['OWN_CAR_AGE'] = app_train['OWN_CAR_AGE'].fillna(app_train['OWN_CAR_AGE'].median())
app_train['APARTMENTS_AVG'] = app_train['APARTMENTS_AVG'].fillna(app_train['APARTMENTS_AVG'].median())
app_train['BASEMENTAREA_AVG'] = app_train['BASEMENTAREA_AVG'].fillna(app_train['BASEMENTAREA_AVG'].median())
app_train['YEARS_BEGINEXPLUATATION_AVG'] = app_train['YEARS_BEGINEXPLUATATION_AVG'].fillna(app_train['YEARS_BEGINEXPLUATATION_AVG'].median())
app_train['YEARS_BUILD_AVG'] = app_train['YEARS_BUILD_AVG'].fillna(app_train['YEARS_BUILD_AVG'].median())
app_train['COMMONAREA_AVG'] = app_train['COMMONAREA_AVG'].fillna(app_train['COMMONAREA_AVG'].median())
app_train['ELEVATORS_AVG'] = app_train['ELEVATORS_AVG'].fillna(app_train['ELEVATORS_AVG'].median())
app_train['ENTRANCES_AVG'] = app_train['ENTRANCES_AVG'].fillna(app_train['ENTRANCES_AVG'].median())
app_train['FLOORSMAX_AVG'] = app_train['FLOORSMAX_AVG'].fillna(app_train['FLOORSMAX_AVG'].median())
app_train['FLOORSMIN_AVG'] = app_train['FLOORSMIN_AVG'].fillna(app_train['FLOORSMIN_AVG'].median())
app_train['LANDAREA_AVG'] = app_train['LANDAREA_AVG'].fillna(app_train['LANDAREA_AVG'].median())
app_train['NONLIVINGAPARTMENTS_AVG'] = app_train['NONLIVINGAPARTMENTS_AVG'].fillna(app_train['NONLIVINGAPARTMENTS_AVG'].median())
app_train['NONLIVINGAREA_AVG'] = app_train['NONLIVINGAREA_AVG'].fillna(app_train['NONLIVINGAREA_AVG'].median())
app_train['EXT_SOURCE_1'] = app_train['EXT_SOURCE_1'].fillna(app_train['EXT_SOURCE_1'].median())
app_train['EXT_SOURCE_2'] = app_train['EXT_SOURCE_2'].fillna(app_train['EXT_SOURCE_2'].median())
app_train['EXT_SOURCE_3'] = app_train['EXT_SOURCE_3'].fillna(app_train['EXT_SOURCE_3'].median())

In [159]:
app_train.OBS_30_CNT_SOCIAL_CIRCLE=app_train.OBS_30_CNT_SOCIAL_CIRCLE.fillna(0)
app_train.DEF_30_CNT_SOCIAL_CIRCLE=app_train.DEF_30_CNT_SOCIAL_CIRCLE.fillna(0)
app_train.DEF_60_CNT_SOCIAL_CIRCLE=app_train.DEF_60_CNT_SOCIAL_CIRCLE.fillna(0)
app_train.DAYS_LAST_PHONE_CHANGE=app_train.DAYS_LAST_PHONE_CHANGE.fillna(0)

In [160]:
app_train.isnull().sum().sum()

0

## Adding new feature

In [162]:
app_train['LOAN_RATE'] = app_train['AMT_ANNUITY'] / app_train['AMT_CREDIT'] 
app_train['CREDIT_INCOME_RATIO'] = app_train['AMT_CREDIT'] / (1 + app_train['AMT_INCOME_TOTAL'])
app_train['EMPLOYED_BIRTH_RATIO'] = app_train['DAYS_EMPLOYED'] / app_train['DAYS_BIRTH']
app_train['EXT_SOURCE_SUM'] = app_train[['EXT_SOURCE_1', 'EXT_SOURCE_2', 'EXT_SOURCE_3']].sum(axis = 1)
app_train['EXT_SOURCE_MEAN'] = app_train[['EXT_SOURCE_1', 'EXT_SOURCE_2', 'EXT_SOURCE_3']].mean(axis = 1)
app_train['EXT_SOURCE_PROD'] = app_train['EXT_SOURCE_1'] * app_train['EXT_SOURCE_2'] * app_train['EXT_SOURCE_3']
app_train['EXT_SOURCE_STD'] = app_train[['EXT_SOURCE_1', 'EXT_SOURCE_2', 'EXT_SOURCE_3']].std(axis=1)
app_train['INCOME_PER_PERSON'] = app_train['AMT_INCOME_TOTAL'] / (1+app_train['CNT_FAM_MEMBERS'])
app_train['INCOME_PER_CHLD'] = app_train['AMT_INCOME_TOTAL'] / (1 + app_train['CNT_CHILDREN'])
app_train['ANNUITY_TO_INCOME_RATIO'] = app_train['AMT_ANNUITY'] / (1 + app_train['AMT_INCOME_TOTAL'])

LOAN_RATE: The ratio of the annuity amount (AMT_ANNUITY) to the credit amount (AMT_CREDIT), representing loan payment burden.

CREDIT_INCOME_RATIO: The ratio of the credit amount to the total income, providing insights into credit load relative to income.

EMPLOYED_BIRTH_RATIO: The ratio of days employed to days since birth, indicating the proportion of life spent working.

EXT_SOURCE_SUM: The sum of three external source features, providing a combined score.

EXT_SOURCE_MEAN: The mean of three external source features, offering a general external source score.

EXT_SOURCE_PROD: The product of the three external source features, capturing their joint effect.

EXT_SOURCE_STD: The standard deviation of the three external source features, indicating variability.

INCOME_PER_PERSON: The income per family member, showing income distribution across the family.

INCOME_PER_CHLD: The income per child, indicating income distribution for child dependents.

ANNUITY_TO_INCOME_RATIO: The ratio of annuity to total income, assessing the financial strain of loan repayments relative to income.

In [163]:
app_train.isnull().sum().sum()

0

In [164]:
app_train

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0           100002       1         Cash loans           M            N   
1           100003       0         Cash loans           F            N   
2           100004       0    Revolving loans           M            Y   
3           100006       0         Cash loans           F            N   
4           100007       0         Cash loans           M            N   
...            ...     ...                ...         ...          ...   
307506      456251       0         Cash loans           M            N   
307507      456252       0         Cash loans           F            N   
307508      456253       0         Cash loans           F            N   
307509      456254       1         Cash loans           F            N   
307510      456255       0         Cash loans           F            N   

       FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
0                    Y             0          202500.0    406597.5   
1                    N             0          270000.0   1293502.5   
2                    Y             0           67500.0    135000.0   
3                    Y             0          135000.0    312682.5   
4                    Y             0          121500.0    513000.0   
...                ...           ...               ...         ...   
307506               N             0          157500.0    254700.0   
307507               Y             0           72000.0    269550.0   
307508               Y             0          153000.0    677664.0   
307509               Y             0          171000.0    370107.0   
307510               N             0          157500.0    675000.0   

        AMT_ANNUITY NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
0           24700.5   Unaccompanied               Working   
1           35698.5          Family         State servant   
2            6750.0   Unaccompanied               Working   
3           29686.5   Unaccompanied               Working   
4           21865.5   Unaccompanied               Working   
...             ...             ...                   ...   
307506      27558.0   Unaccompanied               Working   
307507      12001.5   Unaccompanied             Pensioner   
307508      29979.0   Unaccompanied               Working   
307509      20205.0   Unaccompanied  Commercial associate   
307510      49117.5   Unaccompanied  Commercial associate   

                  NAME_EDUCATION_TYPE    NAME_FAMILY_STATUS  \
0       Secondary / secondary special  Single / not married   
1                    Higher education               Married   
2       Secondary / secondary special  Single / not married   
3       Secondary / secondary special        Civil marriage   
4       Secondary / secondary special  Single / not married   
...                               ...                   ...   
307506  Secondary / secondary special             Separated   
307507  Secondary / secondary special                 Widow   
307508               Higher education             Separated   
307509  Secondary / secondary special               Married   
307510               Higher education               Married   

        NAME_HOUSING_TYPE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
0       House / apartment                    0.018801       -9461   
1       House / apartment                    0.003541      -16765   
2       House / apartment                    0.010032      -19046   
3       House / apartment                    0.008019      -19005   
4       House / apartment                    0.028663      -19932   
...                   ...                         ...         ...   
307506       With parents                    0.032561       -9327   
307507  House / apartment                    0.025164      -20775   
307508  House / apartment                    0.005002      -14966   
307509  House / apartment                    0.005313      -11961   
307510  House / apartment    

## Encoding

In [166]:
app_train.CODE_GENDER=app_train.CODE_GENDER.map({'F':1,'M':0})
app_train.FLAG_OWN_CAR=app_train.FLAG_OWN_CAR.map({'Y':1,'N':0})
app_train.FLAG_OWN_REALTY=app_train.FLAG_OWN_REALTY.map({'Y':1,'N':0})
app_train.EMERGENCYSTATE_MODE=app_train.EMERGENCYSTATE_MODE.map({'Yes':1,'No':0})
app_train, app_train_cat = one_hot_encoder(app_train) 

In [167]:
app_train

SK_ID_CURR  TARGET  CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  \
0           100002       1            0             0                1   
1           100003       0            1             0                0   
2           100004       0            0             1                1   
3           100006       0            1             0                1   
4           100007       0            0             0                1   
...            ...     ...          ...           ...              ...   
307506      456251       0            0             0                0   
307507      456252       0            1             0                1   
307508      456253       0            1             0                1   
307509      456254       1            1             0                1   
307510      456255       0            1             0                0   

        CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0                  0          202500.0    406597.5      24700.5   
1                  0          270000.0   1293502.5      35698.5   
2                  0           67500.0    135000.0       6750.0   
3                  0          135000.0    312682.5      29686.5   
4                  0          121500.0    513000.0      21865.5   
...              ...               ...         ...          ...   
307506             0          157500.0    254700.0      27558.0   
307507             0           72000.0    269550.0      12001.5   
307508             0          153000.0    677664.0      29979.0   
307509             0          171000.0    370107.0      20205.0   
307510             0          157500.0    675000.0      49117.5   

        REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0                         0.018801       -9461         -637.0   
1                         0.003541      -16765        -1188.0   
2                         0.010032      -19046         -225.0   
3                         0.008019      -19005        -3039.0   
4                         0.028663      -19932        -3038.0   
...                            ...         ...            ...   
307506                    0.032561       -9327         -236.0   
307507                    0.025164      -20775        -1648.0   
307508                    0.005002      -14966        -7921.0   
307509                    0.005313      -11961        -4786.0   
307510                    0.046220      -16856        -1262.0   

        DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
0                 -3648.0            -2120          9.0           1   
1                 -1186.0             -291          9.0           1   
2                 -4260.0            -2531         26.0           1   
3                 -9833.0            -2437          9.0           1   
4                 -4311.0            -3458          9.0           1   
...                   ...              ...          ...         ...   
307506            -8456.0            -1982          9.0           1   
307507            -4388.0            -4090          9.0           1   
307508            -6737.0            -5150          9.0           1   
307509            -2562.0             -931          9.0           1   
307510            -5128.0             -410          9.0           1   

        FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
0                    1                0                 1           1   
1                    1                0                 1           1   
2                    1                1                 1           1   
3                    1                0                 1           0   
4                    1                0                 1           0   
...                ...              ...               ...         ...   
307506               1                0                 1           0   
307507               0                0                 1           1   
307508               1 

In [168]:
app_train_cat

['NAME_CONTRACT_TYPE_Cash loans',
 'NAME_CONTRACT_TYPE_Revolving loans',
 'NAME_TYPE_SUITE_Children',
 'NAME_TYPE_SUITE_Family',
 'NAME_TYPE_SUITE_Group of people',
 'NAME_TYPE_SUITE_Other_A',
 'NAME_TYPE_SUITE_Other_B',
 'NAME_TYPE_SUITE_Spouse, partner',
 'NAME_TYPE_SUITE_Unaccompanied',
 'NAME_INCOME_TYPE_Businessman',
 'NAME_INCOME_TYPE_Commercial associate',
 'NAME_INCOME_TYPE_Maternity leave',
 'NAME_INCOME_TYPE_Pensioner',
 'NAME_INCOME_TYPE_State servant',
 'NAME_INCOME_TYPE_Student',
 'NAME_INCOME_TYPE_Unemployed',
 'NAME_INCOME_TYPE_Working',
 'NAME_EDUCATION_TYPE_Academic degree',
 'NAME_EDUCATION_TYPE_Higher education',
 'NAME_EDUCATION_TYPE_Incomplete higher',
 'NAME_EDUCATION_TYPE_Lower secondary',
 'NAME_EDUCATION_TYPE_Secondary / secondary special',
 'NAME_FAMILY_STATUS_Civil marriage',
 'NAME_FAMILY_STATUS_Married',
 'NAME_FAMILY_STATUS_Separated',
 'NAME_FAMILY_STATUS_Single / not married',
 'NAME_FAMILY_STATUS_Unknown',
 'NAME_FAMILY_STATUS_Widow',
 'NAME_HOUSING_TYP

In [169]:
app_train.columns

Index(['SK_ID_CURR', 'TARGET', 'CODE_GENDER', 'FLAG_OWN_CAR',
       'FLAG_OWN_REALTY', 'CNT_CHILDREN', 'AMT_INCOME_TOTAL', 'AMT_CREDIT',
       'AMT_ANNUITY', 'REGION_POPULATION_RELATIVE',
       ...
       'HOUSETYPE_MODE_block of flats', 'HOUSETYPE_MODE_specific housing',
       'HOUSETYPE_MODE_terraced house', 'WALLSMATERIAL_MODE_Block',
       'WALLSMATERIAL_MODE_Mixed', 'WALLSMATERIAL_MODE_Monolithic',
       'WALLSMATERIAL_MODE_Others', 'WALLSMATERIAL_MODE_Panel',
       'WALLSMATERIAL_MODE_Stone, brick', 'WALLSMATERIAL_MODE_Wooden'],
      dtype='object', length=217)

In [170]:
_, idx = np.unique(app_train.columns, return_index=True)

# Select columns using the unique indices
app_train = app_train.iloc[:, np.sort(idx)]
app_train

SK_ID_CURR  TARGET  CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  \
0           100002       1            0             0                1   
1           100003       0            1             0                0   
2           100004       0            0             1                1   
3           100006       0            1             0                1   
4           100007       0            0             0                1   
...            ...     ...          ...           ...              ...   
307506      456251       0            0             0                0   
307507      456252       0            1             0                1   
307508      456253       0            1             0                1   
307509      456254       1            1             0                1   
307510      456255       0            1             0                0   

        CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0                  0          202500.0    406597.5      24700.5   
1                  0          270000.0   1293502.5      35698.5   
2                  0           67500.0    135000.0       6750.0   
3                  0          135000.0    312682.5      29686.5   
4                  0          121500.0    513000.0      21865.5   
...              ...               ...         ...          ...   
307506             0          157500.0    254700.0      27558.0   
307507             0           72000.0    269550.0      12001.5   
307508             0          153000.0    677664.0      29979.0   
307509             0          171000.0    370107.0      20205.0   
307510             0          157500.0    675000.0      49117.5   

        REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0                         0.018801       -9461         -637.0   
1                         0.003541      -16765        -1188.0   
2                         0.010032      -19046         -225.0   
3                         0.008019      -19005        -3039.0   
4                         0.028663      -19932        -3038.0   
...                            ...         ...            ...   
307506                    0.032561       -9327         -236.0   
307507                    0.025164      -20775        -1648.0   
307508                    0.005002      -14966        -7921.0   
307509                    0.005313      -11961        -4786.0   
307510                    0.046220      -16856        -1262.0   

        DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
0                 -3648.0            -2120          9.0           1   
1                 -1186.0             -291          9.0           1   
2                 -4260.0            -2531         26.0           1   
3                 -9833.0            -2437          9.0           1   
4                 -4311.0            -3458          9.0           1   
...                   ...              ...          ...         ...   
307506            -8456.0            -1982          9.0           1   
307507            -4388.0            -4090          9.0           1   
307508            -6737.0            -5150          9.0           1   
307509            -2562.0             -931          9.0           1   
307510            -5128.0             -410          9.0           1   

        FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
0                    1                0                 1           1   
1                    1                0                 1           1   
2                    1                1                 1           1   
3                    1                0                 1           0   
4                    1                0                 1           0   
...                ...              ...               ...         ...   
307506               1                0                 1           0   
307507               0                0                 1           1   
307508               1 

In [171]:
pd.set_option('display.max_rows',None) 

In [172]:
app_train.std()

SK_ID_CURR                                           102790.132982
TARGET                                                    0.272420
CODE_GENDER                                               0.474263
FLAG_OWN_CAR                                              0.473745
FLAG_OWN_REALTY                                           0.460970
CNT_CHILDREN                                              0.719314
AMT_INCOME_TOTAL                                     108812.210716
AMT_CREDIT                                           402012.635815
AMT_ANNUITY                                           14487.539311
REGION_POPULATION_RELATIVE                                0.010785
DAYS_BIRTH                                             4363.982424
DAYS_EMPLOYED                                          2136.160141
DAYS_REGISTRATION                                      3522.883030
DAYS_ID_PUBLISH                                        1509.454566
OWN_CAR_AGE                                               4.28

In [173]:
pd.reset_option('display.max_rows') 

In [174]:
app_train.isnull().sum().sum()

0

In [175]:
gc.enable()
del corr_matrix,upper,to_drop 
gc.collect()

0

## Adding all csv files 

In [177]:
app = app_train.copy()
app = app.set_index('SK_ID_CURR')

In [178]:
app = app.merge(pos_cash_balance_agg, on = 'SK_ID_CURR', how = 'left')

In [179]:
app = app.merge(installments_payments_agg, on = 'SK_ID_CURR', how = 'left')
app = app.merge(previous_application_agg, on = 'SK_ID_CURR', how = 'left')
app = app.merge(bureau_agg, on = 'SK_ID_CURR', how = 'left')
app = app.merge(credit_card_balance_agg, on = 'SK_ID_CURR', how = 'left')
app.reset_index(inplace = True)

In [180]:
gc.enable()
del app_train,pos_cash_balance_agg,installments_payments_agg,previous_application_agg,bureau_agg,credit_card_balance_agg
gc.collect()

0

## Final preprocessing

In [182]:
app

SK_ID_CURR  TARGET  CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  \
0           100002       1            0             0                1   
1           100003       0            1             0                0   
2           100004       0            0             1                1   
3           100006       0            1             0                1   
4           100007       0            0             0                1   
...            ...     ...          ...           ...              ...   
307502      456251       0            0             0                0   
307503      456252       0            1             0                1   
307504      456253       0            1             0                1   
307505      456254       1            1             0                1   
307506      456255       0            1             0                0   

        CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0                  0          202500.0    406597.5      24700.5   
1                  0          270000.0   1293502.5      35698.5   
2                  0           67500.0    135000.0       6750.0   
3                  0          135000.0    312682.5      29686.5   
4                  0          121500.0    513000.0      21865.5   
...              ...               ...         ...          ...   
307502             0          157500.0    254700.0      27558.0   
307503             0           72000.0    269550.0      12001.5   
307504             0          153000.0    677664.0      29979.0   
307505             0          171000.0    370107.0      20205.0   
307506             0          157500.0    675000.0      49117.5   

        REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0                         0.018801       -9461         -637.0   
1                         0.003541      -16765        -1188.0   
2                         0.010032      -19046         -225.0   
3                         0.008019      -19005        -3039.0   
4                         0.028663      -19932        -3038.0   
...                            ...         ...            ...   
307502                    0.032561       -9327         -236.0   
307503                    0.025164      -20775        -1648.0   
307504                    0.005002      -14966        -7921.0   
307505                    0.005313      -11961        -4786.0   
307506                    0.046220      -16856        -1262.0   

        DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
0                 -3648.0            -2120          9.0           1   
1                 -1186.0             -291          9.0           1   
2                 -4260.0            -2531         26.0           1   
3                 -9833.0            -2437          9.0           1   
4                 -4311.0            -3458          9.0           1   
...                   ...              ...          ...         ...   
307502            -8456.0            -1982          9.0           1   
307503            -4388.0            -4090          9.0           1   
307504            -6737.0            -5150          9.0           1   
307505            -2562.0             -931          9.0           1   
307506            -5128.0             -410          9.0           1   

        FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
0                    1                0                 1           1   
1                    1                0                 1           1   
2                    1                1                 1           1   
3                    1                0                 1           0   
4                    1                0                 1           0   
...                ...              ...               ...         ...   
307502               1                0                 1           0   
307503               0                0                 1           1   
307504               1 

In [183]:
app.duplicated().sum()


0

In [184]:
pd.set_option('display.max_rows',None) 

In [185]:
app.std()

SK_ID_CURR                                                                                102790.132982
TARGET                                                                                          0.27242
CODE_GENDER                                                                                    0.474263
FLAG_OWN_CAR                                                                                   0.473745
FLAG_OWN_REALTY                                                                                 0.46097
CNT_CHILDREN                                                                                   0.719314
AMT_INCOME_TOTAL                                                                          108812.210716
AMT_CREDIT                                                                                402012.635815
AMT_ANNUITY                                                                                14487.539311
REGION_POPULATION_RELATIVE                                      

In [186]:
pd.reset_option('display.max_rows')

In [187]:
app=app.drop(columns=['previous_application_NAME_GOODS_CATEGORY_House Construction_MEAN','previous_application_NAME_GOODS_CATEGORY_House Construction_SUM','bureau_CREDIT_TYPE_Loan for working capital replenishment_MIN','credit_card_balance_CNT_DRAWINGS_OTHER_CURRENT_MIN'])
app.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 307507 entries, 0 to 307506
Columns: 763 entries, SK_ID_CURR to credit_card_balance_AMT_CREDIT_LIMIT_ACTUAL_MAX
dtypes: bool(131), float64(556), int64(43), object(33)
memory usage: 1.5+ GB


## Correlation

In [189]:

# Threshold for removing correlated variables
threshold = 0.9

# Absolute value correlation matrix
corr_matrix = app.corr().abs()
corr_matrix.head()

SK_ID_CURR    TARGET  CODE_GENDER  FLAG_OWN_CAR  \
SK_ID_CURR         1.000000  0.002111     0.000735      0.001215   
TARGET             0.002111  1.000000     0.054710      0.021850   
CODE_GENDER        0.000735  0.054710     1.000000      0.345848   
FLAG_OWN_CAR       0.001215  0.021850     0.345848      1.000000   
FLAG_OWN_REALTY    0.000710  0.006146     0.044374      0.002820   

                 FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR              0.000710      0.001353          0.001578    0.000298   
TARGET                  0.006146      0.019371          0.020461    0.030427   
CODE_GENDER             0.044374      0.047698          0.165369    0.021467   
FLAG_OWN_CAR            0.002820      0.102427          0.184212    0.116268   
FLAG_OWN_REALTY         1.000000      0.002345          0.004072    0.039069   

                 AMT_ANNUITY  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
SK_ID_CURR          0.000359                    0.000293    0.001500   
TARGET              0.012806                    0.027244    0.078242   
CODE_GENDER         0.076948                    0.006901    0.148067   
FLAG_OWN_CAR        0.141573                    0.041439    0.129883   
FLAG_OWN_REALTY     0.005138                    0.025216    0.119152   

                 DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  \
SK_ID_CURR            0.000090           0.000973         0.000389   
TARGET                0.063366           0.041976         0.051457   
CODE_GENDER           0.064046           0.077187         0.000132   
FLAG_OWN_CAR          0.000699           0.087778         0.013661   
FLAG_OWN_REALTY       0.018595           0.025226         0.006664   

                 OWN_CAR_AGE  FLAG_MOBIL  FLAG_EMP_PHONE  FLAG_WORK_PHONE  \
SK_ID_CURR          0.001300    0.002804        0.001332         0.000395   
TARGET              0.024909    0.000534        0.045984         0.028533   
CODE_GENDER         0.096446    0.002503        0.157245         0.033942   
FLAG_OWN_CAR        0.143429    0.002512        0.154659         0.011463   
FLAG_OWN_REALTY     0.013196    0.001198        0.070026         0.114064   

                 FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  CNT_FAM_MEMBERS  \
SK_ID_CURR               0.002815    0.002769    0.000278         0.003068   
TARGET                   0.000370    0.023801    0.001759         0.009409   
CODE_GENDER              0.006020    0.019503    0.018231         0.080888   
FLAG_OWN_CAR             0.006644    0.007595    0.032106         0.150279   
FLAG_OWN_REALTY          0.008526    0.041521    0.029249         0.007427   

                 REGION_RATING_CLIENT  HOUR_APPR_PROCESS_START  \
SK_ID_CURR                   0.001067                 0.000354   
TARGET                       0.058901                 0.024164   
CODE_GENDER                  0.017881                 0.007151   
FLAG_OWN_CAR                 0.022676                 0.014373   
FLAG_OWN_REALTY              0.001285                 0.102693   

                 REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
SK_ID_CURR                         0.000284                    0.001095   
TARGET                             0.005575                    0.006941   
CODE_GENDER                        0.023690                    0.103456   
FLAG_OWN_CAR                       0.000667                    0.038938   
FLAG_OWN_REALTY                    0.036300                    0.032314   

                 LIVE_REGION_NOT_WORK_REGION  REG_CITY_NOT_LIVE_CITY  \
SK_ID_CURR                          0.002901                0.001888   
TARGET                              0.002819                0.044394   
CODE_GENDER                         0.106078                0.048254   
FLAG_OWN_CAR                        0.046353                0.003125   
FLAG_OWN_REALTY                     0.018322                0.061707   

                 REG_CITY_NOT_WORK_CITY  LIVE_CITY_NOT_WORK_

In [190]:
upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))
upper.head()

SK_ID_CURR    TARGET  CODE_GENDER  FLAG_OWN_CAR  \
SK_ID_CURR              NaN  0.002111     0.000735      0.001215   
TARGET                  NaN       NaN     0.054710      0.021850   
CODE_GENDER             NaN       NaN          NaN      0.345848   
FLAG_OWN_CAR            NaN       NaN          NaN           NaN   
FLAG_OWN_REALTY         NaN       NaN          NaN           NaN   

                 FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR              0.000710      0.001353          0.001578    0.000298   
TARGET                  0.006146      0.019371          0.020461    0.030427   
CODE_GENDER             0.044374      0.047698          0.165369    0.021467   
FLAG_OWN_CAR            0.002820      0.102427          0.184212    0.116268   
FLAG_OWN_REALTY              NaN      0.002345          0.004072    0.039069   

                 AMT_ANNUITY  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
SK_ID_CURR          0.000359                    0.000293    0.001500   
TARGET              0.012806                    0.027244    0.078242   
CODE_GENDER         0.076948                    0.006901    0.148067   
FLAG_OWN_CAR        0.141573                    0.041439    0.129883   
FLAG_OWN_REALTY     0.005138                    0.025216    0.119152   

                 DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  \
SK_ID_CURR            0.000090           0.000973         0.000389   
TARGET                0.063366           0.041976         0.051457   
CODE_GENDER           0.064046           0.077187         0.000132   
FLAG_OWN_CAR          0.000699           0.087778         0.013661   
FLAG_OWN_REALTY       0.018595           0.025226         0.006664   

                 OWN_CAR_AGE  FLAG_MOBIL  FLAG_EMP_PHONE  FLAG_WORK_PHONE  \
SK_ID_CURR          0.001300    0.002804        0.001332         0.000395   
TARGET              0.024909    0.000534        0.045984         0.028533   
CODE_GENDER         0.096446    0.002503        0.157245         0.033942   
FLAG_OWN_CAR        0.143429    0.002512        0.154659         0.011463   
FLAG_OWN_REALTY     0.013196    0.001198        0.070026         0.114064   

                 FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  CNT_FAM_MEMBERS  \
SK_ID_CURR               0.002815    0.002769    0.000278         0.003068   
TARGET                   0.000370    0.023801    0.001759         0.009409   
CODE_GENDER              0.006020    0.019503    0.018231         0.080888   
FLAG_OWN_CAR             0.006644    0.007595    0.032106         0.150279   
FLAG_OWN_REALTY          0.008526    0.041521    0.029249         0.007427   

                 REGION_RATING_CLIENT  HOUR_APPR_PROCESS_START  \
SK_ID_CURR                   0.001067                 0.000354   
TARGET                       0.058901                 0.024164   
CODE_GENDER                  0.017881                 0.007151   
FLAG_OWN_CAR                 0.022676                 0.014373   
FLAG_OWN_REALTY              0.001285                 0.102693   

                 REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
SK_ID_CURR                         0.000284                    0.001095   
TARGET                             0.005575                    0.006941   
CODE_GENDER                        0.023690                    0.103456   
FLAG_OWN_CAR                       0.000667                    0.038938   
FLAG_OWN_REALTY                    0.036300                    0.032314   

                 LIVE_REGION_NOT_WORK_REGION  REG_CITY_NOT_LIVE_CITY  \
SK_ID_CURR                          0.002901                0.001888   
TARGET                              0.002819                0.044394   
CODE_GENDER                         0.106078                0.048254   
FLAG_OWN_CAR                        0.046353                0.003125   
FLAG_OWN_REALTY                     0.018322                0.061707   

                 REG_CITY_NOT_WORK_CITY  LIVE_CITY_NOT_WORK_

In [191]:
to_drop = [column for column in upper.columns if any(upper[column] > threshold)]

print('There are %d columns to remove.' % (len(to_drop)))

There are 94 columns to remove.


In [192]:
to_drop 

['EMPLOYED_BIRTH_RATIO',
 'EXT_SOURCE_MEAN',
 'EXT_SOURCE_PROD',
 'INCOME_PER_CHLD',
 'NAME_CONTRACT_TYPE_Revolving loans',
 'NAME_INCOME_TYPE_Pensioner',
 'ORGANIZATION_TYPE_XNA',
 'pos_cash_balance_INSTALLMENTS_PAID_MAX',
 'pos_cash_balance_CNT_INSTALMENT_MEAN',
 'pos_cash_balance_CNT_INSTALMENT_MAX',
 'pos_cash_balance_SK_DPD_DEF_MAX',
 'pos_cash_balance_SK_DPD_MAX',
 'pos_cash_balance_NAME_CONTRACT_STATUS_SUM',
 'installments_payments_DAYS_INSTALMENT_MIN',
 'installments_payments_DAYS_INSTALMENT_MEAN',
 'previous_application_DAYS_DECISION_MIN',
 'previous_application_NAME_GOODS_CATEGORY_Animals_SUM',
 'previous_application_NAME_PORTFOLIO_Cars_MEAN',
 'previous_application_NAME_PORTFOLIO_Cars_SUM',
 'previous_application_NAME_GOODS_CATEGORY_Clothing and Accessories_MEAN',
 'previous_application_NAME_GOODS_CATEGORY_Clothing and Accessories_SUM',
 'previous_application_NAME_CONTRACT_TYPE_Revolving loans_MEAN',
 'previous_application_NAME_PORTFOLIO_XNA_SUM',
 'previous_application_NAME

In [193]:
app = app.drop(columns = to_drop)

## Missing values

In [195]:
app_missing = (app.isnull().sum() / len(app)).sort_values(ascending = False)
app_missing.head()

credit_card_balance_AMT_CREDIT_LIMIT_ACTUAL_MEAN       0.717389
credit_card_balance_AMT_DRAWINGS_ATM_CURRENT_MIN       0.717389
credit_card_balance_AMT_DRAWINGS_POS_CURRENT_MEAN      0.717389
credit_card_balance_AMT_DRAWINGS_OTHER_CURRENT_MAX     0.717389
credit_card_balance_AMT_DRAWINGS_OTHER_CURRENT_MEAN    0.717389
dtype: float64

In [196]:
app_missing = app_missing.index[app_missing > 0.70]
print(len(app_missing))

37


In [197]:
app = app.drop(columns = app_missing)
app = app.fillna(0)
app.head(30)

SK_ID_CURR  TARGET  CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  \
0       100002       1            0             0                1   
1       100003       0            1             0                0   
2       100004       0            0             1                1   
3       100006       0            1             0                1   
4       100007       0            0             0                1   
5       100008       0            0             0                1   
6       100009       0            1             1                1   
7       100010       0            0             1                1   
8       100011       0            1             0                1   
9       100012       0            0             0                1   
10      100014       0            1             0                1   
11      100015       0            1             0                1   
12      100016       0            1             0                1   
13      100017       0            0             1                0   
14      100018       0            1             0                1   
15      100019       0            0             1                1   
16      100020       0            0             0                0   
17      100021       0            1             0                1   
18      100022       0            1             0                1   
19      100023       0            1             0                1   
20      100024       0            0             1                1   
21      100025       0            1             1                1   
22      100026       0            1             0                0   
23      100027       0            1             0                1   
24      100029       0            0             1                0   
25      100030       0            1             0                1   
26      100031       1            1             0                1   
27      100032       0            0             0                1   
28      100033       0            0             1                1   
29      100034       0            0             0                1   

    CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0              0        202500.000    406597.5      24700.5   
1              0        270000.000   1293502.5      35698.5   
2              0         67500.000    135000.0       6750.0   
3              0        135000.000    312682.5      29686.5   
4              0        121500.000    513000.0      21865.5   
5              0         99000.000    490495.5      27517.5   
6              1        171000.000   1560726.0      41301.0   
7              0        360000.000   1530000.0      42075.0   
8              0        112500.000   1019610.0      33826.5   
9              0        135000.000    405000.0      20250.0   
10             1        112500.000    652500.0      21177.0   
11             0         38419.155    148365.0      10678.5   
12             0         67500.000     80865.0       5881.5   
13             1        225000.000    918468.0      28966.5   
14             0        189000.000    773680.5      32778.0   
15             0        157500.000    299772.0      20160.0   
16             0        108000.000    509602.5      26149.5   
17             1         81000.000    270000.0      13500.0   
18             0        112500.000    157500.0       7875.0   
19             1         90000.000    544491.0      17563.5   
20             0        135000.000    427500.0      21375.0   
21             1        202500.000   1132573.5      37561.5   
22             1        450000.000    497520.0      32521.5   
23             0         83250.000    239850.0      23850.0   
24             2        135000.000    247500.0      12703.5   
25             0         90000.000    225000.0      11074.5   
26             0        112500.000    979992.0      27076.5   
27             1        112500.000    327024.0      23827.5   
28    

In [198]:
app_fe=[feature for feature in app.columns if feature not in ['SK_ID_CURR','TARGET']]
app_fe

['CODE_GENDER',
 'FLAG_OWN_CAR',
 'FLAG_OWN_REALTY',
 'CNT_CHILDREN',
 'AMT_INCOME_TOTAL',
 'AMT_CREDIT',
 'AMT_ANNUITY',
 'REGION_POPULATION_RELATIVE',
 'DAYS_BIRTH',
 'DAYS_EMPLOYED',
 'DAYS_REGISTRATION',
 'DAYS_ID_PUBLISH',
 'OWN_CAR_AGE',
 'FLAG_MOBIL',
 'FLAG_EMP_PHONE',
 'FLAG_WORK_PHONE',
 'FLAG_CONT_MOBILE',
 'FLAG_PHONE',
 'FLAG_EMAIL',
 'CNT_FAM_MEMBERS',
 'REGION_RATING_CLIENT',
 'HOUR_APPR_PROCESS_START',
 'REG_REGION_NOT_LIVE_REGION',
 'REG_REGION_NOT_WORK_REGION',
 'LIVE_REGION_NOT_WORK_REGION',
 'REG_CITY_NOT_LIVE_CITY',
 'REG_CITY_NOT_WORK_CITY',
 'LIVE_CITY_NOT_WORK_CITY',
 'EXT_SOURCE_1',
 'EXT_SOURCE_2',
 'EXT_SOURCE_3',
 'APARTMENTS_AVG',
 'BASEMENTAREA_AVG',
 'YEARS_BEGINEXPLUATATION_AVG',
 'YEARS_BUILD_AVG',
 'COMMONAREA_AVG',
 'ELEVATORS_AVG',
 'ENTRANCES_AVG',
 'FLOORSMAX_AVG',
 'FLOORSMIN_AVG',
 'LANDAREA_AVG',
 'NONLIVINGAPARTMENTS_AVG',
 'NONLIVINGAREA_AVG',
 'EMERGENCYSTATE_MODE',
 'OBS_30_CNT_SOCIAL_CIRCLE',
 'DEF_30_CNT_SOCIAL_CIRCLE',
 'DEF_60_CNT_SOCIAL

In [199]:
for feature in app_fe :
    app[feature]=app[feature].abs()

In [200]:
log_fe=[feature for feature in app_fe if feature not in app_train_cat] # Remove OHE features


In [201]:
# List of feautures which are actually categorical but shown as numerical features (derived from our EDA part)
remove_cols=['FLAG_MOBIL','FLAG_EMP_PHONE','FLAG_WORK_PHONE','FLAG_CONT_MOBILE','FLAG_PHONE','FLAG_EMAIL','REGION_RATING_CLIENT',
 'REGION_RATING_CLIENT_W_CITY','REG_REGION_NOT_LIVE_REGION','REG_REGION_NOT_WORK_REGION','LIVE_REGION_NOT_WORK_REGION',
 'REG_CITY_NOT_LIVE_CITY','REG_CITY_NOT_WORK_CITY','LIVE_CITY_NOT_WORK_CITY','FLAG_DOCUMENT_2','FLAG_DOCUMENT_3','FLAG_DOCUMENT_4',
 'FLAG_DOCUMENT_5','FLAG_DOCUMENT_6','FLAG_DOCUMENT_7','FLAG_DOCUMENT_8','FLAG_DOCUMENT_9','FLAG_DOCUMENT_10','FLAG_DOCUMENT_11',
 'FLAG_DOCUMENT_12','FLAG_DOCUMENT_13','FLAG_DOCUMENT_14','FLAG_DOCUMENT_15','FLAG_DOCUMENT_16','FLAG_DOCUMENT_17',
 'FLAG_DOCUMENT_18','FLAG_DOCUMENT_19','FLAG_DOCUMENT_20','FLAG_DOCUMENT_21']

In [202]:
log_fe_final=[feature for feature in log_fe if feature not in remove_cols]
# Also remove Label Encoded feautures from list
log_fe_final.remove('CODE_GENDER')
log_fe_final.remove('FLAG_OWN_CAR')
log_fe_final.remove('FLAG_OWN_REALTY')
log_fe_final.remove('EMERGENCYSTATE_MODE')

In [203]:
# We will do Log transform of the skewed numerical features to lessen impact of outliers
# As a general rule of thumb, a skewness with an absolute value > 0.5 is considered at least moderately skewed
from scipy.stats import skew

# Ensure the columns are numerical
numerical_data = app[log_fe_final].select_dtypes(include=["number"])

# Handle NaN values (e.g., fill with 0 or drop them)
numerical_data = numerical_data.fillna(0)  # Alternatively, you can use .dropna()

# Compute skewness for numerical features
skewness = numerical_data.apply(lambda x: skew(x))

# Filter features with absolute skewness greater than 0.5
skewness = skewness[abs(skewness) > 0.5]

# Print the result
print(f"{skewness.shape[0]} skewed numerical features to log transform")


421 skewed numerical features to log transform


In [204]:
skewed_features = skewness.index
app[skewed_features] = np.log1p(app[skewed_features])

In [205]:
app

SK_ID_CURR  TARGET  CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  \
0           100002       1            0             0                1   
1           100003       0            1             0                0   
2           100004       0            0             1                1   
3           100006       0            1             0                1   
4           100007       0            0             0                1   
...            ...     ...          ...           ...              ...   
307502      456251       0            0             0                0   
307503      456252       0            1             0                1   
307504      456253       0            1             0                1   
307505      456254       1            1             0                1   
307506      456255       0            1             0                0   

        CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0                0.0         12.218500   12.915581    10.114619   
1                0.0         12.506181   14.072865    10.482892   
2                0.0         11.119898   11.813037     8.817446   
3                0.0         11.813037   12.652947    10.298481   
4                0.0         11.707678   13.148033     9.992711   
...              ...               ...         ...          ...   
307502           0.0         11.967187   12.447846    10.224084   
307503           0.0         11.184435   12.504513     9.392870   
307504           0.0         11.938200   13.426408    10.308286   
307505           0.0         12.049425   12.821550     9.913735   
307506           0.0         11.967187   13.422469    10.801991   

        REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0                         0.018626        9461       6.458338   
1                         0.003535       16765       7.080868   
2                         0.009982       19046       5.420535   
3                         0.007987       19005       8.019613   
4                         0.028260       19932       8.019284   
...                            ...         ...            ...   
307502                    0.032042        9327       5.468060   
307503                    0.024853       20775       7.407924   
307504                    0.004990       14966       8.977399   
307505                    0.005299       11961       8.473659   
307506                    0.045184       16856       7.141245   

        DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
0                8.202208             2120     2.302585           1   
1                7.079184              291     2.302585           1   
2                8.357259             2531     3.295837           1   
3                9.193601             2437     2.302585           1   
4                8.369157             3458     2.302585           1   
...                   ...              ...          ...         ...   
307502           9.042750             1982     2.302585           1   
307503           8.386857             4090     2.302585           1   
307504           8.815518             5150     2.302585           1   
307505           7.848934              931     2.302585           1   
307506           8.542666              410     2.302585           1   

        FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
0                    1                0                 1           1   
1                    1                0                 1           1   
2                    1                1                 1           1   
3                    1                0                 1           0   
4                    1                0                 1           0   
...                ...              ...               ...         ...   
307502               1                0                 1           0   
307503               0                0                 1           1   
307504               1 

In [206]:
app.isnull().sum().sum()

0

In [207]:
pd.set_option('display.max_rows',None)


In [208]:
app.std()

SK_ID_CURR                                                                               102790.132982
TARGET                                                                                         0.27242
CODE_GENDER                                                                                   0.474263
FLAG_OWN_CAR                                                                                  0.473745
FLAG_OWN_REALTY                                                                                0.46097
CNT_CHILDREN                                                                                  0.405804
AMT_INCOME_TOTAL                                                                               0.48876
AMT_CREDIT                                                                                    0.715093
AMT_ANNUITY                                                                                   0.545857
REGION_POPULATION_RELATIVE                                               

In [209]:
pd.reset_option('display.max_rows')

In [210]:
app=app.drop(columns=['bureau_CREDIT_TYPE_Cash loan (non-earmarked)_MIN'])
app.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 307507 entries, 0 to 307506
Columns: 631 entries, SK_ID_CURR to bureau_bureau_balance_STATUS_MEAN_MIN
dtypes: bool(128), float64(432), int64(42), object(29)
memory usage: 1.2+ GB


## Memory optimization

In [212]:
X=app.drop(columns=['SK_ID_CURR','TARGET'])
y=app.TARGET

In [213]:
gc.enable()
del app,corr_matrix,upper,to_drop,app_missing,app_fe,skewness,skewed_features
gc.collect()

0

In [214]:
import re
X = X.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))

In [215]:
def reduce_mem_usage(df):
    """ iterate through all the columns of a dataframe and modify the data type
        to reduce memory usage.        
    """
    start_mem = df.memory_usage().sum() / 1024**2
    print('Memory usage of dataframe is {:.2f} MB'.format(start_mem))
    
    for col in df.columns:
        col_type = df[col].dtype
        
        if col_type != object:
            c_min = df[col].min()
            c_max = df[col].max()
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)  
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)
        else:
            df[col] = df[col].astype('category')

    end_mem = df.memory_usage().sum() / 1024**2
    print('Memory usage after optimization is: {:.2f} MB'.format(end_mem))
    print('Decreased by {:.1f}%'.format(100 * (start_mem - end_mem) / start_mem))
    
    return df

In [216]:
X = reduce_mem_usage(X)

Memory usage of dataframe is 1212.93 MB
Memory usage after optimization is: 349.28 MB
Decreased by 71.2%


we optimized the memory so as to reduce the computational time which would largely affect the cpu memory usage

## Saving files as csv

In [217]:
X.to_csv('X.csv',index=False)

In [218]:
y.to_csv('y.csv',index=False)